<h1 id="tocheading">Table of Contents</h1>
<div id="toc"></div>

In [2]:
%%javascript
$.getScript('https://kmahelona.github.io/ipython_notebook_goodies/ipython_notebook_toc.js')
$('head').append('<style>table {font-family: "Doulos SIL"; font-size=5em;}')

In [3]:
from IPython.display import display
from IPython.display import HTML
from IPython.display import Image

import csv
import collections
import matplotlib
import random

In [4]:
def get_inventories(aggregated, consonants):
    with open(aggregated) as f:
        aggregated_data = [i for i in csv.DictReader(f, delimiter='\t')]

    with open(consonants) as f:
        segments = [segment for segment in csv.DictReader(f, delimiter='\t')]

    inventories = []
    for inventory in aggregated_data:
        inventory_consonants = int(inventory['Consonants'])
        if inventory_consonants <= 14 and 'dialect' not in inventory['LanguageName']:
            # Get rid of ugly language labels
            lang_name = inventory['LanguageName']
            
            if 'Maxakali' in lang_name:
                continue
                
            if lang_name.isupper() or lang_name.islower():
                inventory['LanguageName'] = inventory['LanguageName'].title()

            # Map the genus to actual language family name
            try:
                inventory['LanguageFamilyRoot'] = genus_to_family[inventory['LanguageFamilyGenus']]
            except KeyError:
                # If the language is unclassified, we'll have to skip it 😢
                continue

            inventory['Segments'] = []
            for segment in segments:
                if inventory['InventoryID'] == segment['InventoryID']:
                    inventory['Segments'].append(segment['Phoneme'])

            for key in ['Phonemes', 'Tones', 'Population', 'Trump', 'Country', 'Vowels']:
                del inventory[key]

            if inventory_consonants != len(inventory['Segments']):
                print('Invalid inv: {}'.format(inventory))
            else:
                inventories.append(inventory)

    else:
        return inventories


def get_features_dict(features_file, phonemes_file):
    with open(phonemes_file) as f:
        phonemes = [i for i in csv.DictReader(f, delimiter='\t')]

    phoneme_classes = {i['Phoneme']: i['CombinedClass'] for i in phonemes}
    
    with open(features_file) as f:
        features = [i for i in csv.DictReader(f, delimiter='\t')]

    features_d = {}

    # NOTE: if we need non-present features, disable deep copy
    for segment in features:
        # Only act on consonants
        if segment['syllabic'] == '+':
            continue
        else:
            segment_copy = {}
            for feature in segment:
                if segment[feature] == '0':
                    segment_copy[feature] = None
                elif segment[feature] == '+':
                    segment_copy[feature] = True
                elif segment[feature] == '-':
                    segment_copy[feature] = False
                elif segment[feature] == '+,-' or segment[feature] == '-,+':
                    segment_copy[feature] = True
                    segment_copy['complex'] = True
            
            try:
                segment_copy['class'] = phoneme_classes[segment['segment']]
            except KeyError:
                segment_copy['class'] = 'c-d-c'
            features_d[segment['segment']] = segment_copy
    
    else:
        return features_d

    
def get_genus_map(family_file, genus_file):
    # Initialise families and genera
    with open(family_file) as f:
        families = [i for i in csv.DictReader(f)]

    with open(genus_file) as f:
        genera = [i for i in csv.DictReader(f)]

    # Map a genus to a family, since the source data provides an ID instead of a pretty name
    families_map = {family['pk']: family['name'] for family in families}
    genus_to_family = {genus['name']: families_map[genus['family_pk']] for genus in genera}
    
    return genus_to_family
        
    
def is_voiced(segment):
    return features_d[segment]['periodicGlottalSource']


def is_plosive(segment):
    is_consonantal = features_d[segment]['consonantal'] is True
    is_not_sonorant = features_d[segment]['sonorant'] is False
    is_not_continuant = features_d[segment]['continuant'] is False
    is_not_strident = features_d[segment]['strident'] is None or features_d[segment]['strident'] is False
    is_not_delayed_release = features_d[segment]['delayedRelease'] is None or features_d[segment]['delayedRelease'] is False
    
    return is_consonantal and is_not_sonorant and is_not_continuant and is_not_strident and is_not_delayed_release


def is_affricate(segment):
    is_consonantal = features_d[segment]['consonantal'] is True
    is_not_sonorant = features_d[segment]['sonorant'] is False
    is_not_continuant = features_d[segment]['continuant'] is False
    is_strident = features_d[segment]['strident'] is True
    
    return is_consonantal and is_not_sonorant and is_not_continuant and is_strident


def is_fricative(segment):
    is_syllabic = features_d[segment]['syllabic'] is False
    is_not_sonorant = features_d[segment]['sonorant'] is False
    is_continuant = features_d[segment]['continuant'] is True
    
    return is_syllabic and is_not_sonorant and is_continuant


def is_nasal(segment):
    is_consonantal = features_d[segment]['consonantal'] is True
    is_nasal = features_d[segment]['nasal'] is True
    is_continuant = features_d[segment]['continuant'] is False
    
    return is_consonantal and is_nasal and is_continuant


def is_liquid(segment):
    is_consonantal = features_d[segment]['consonantal'] is True
    is_continuant = features_d[segment]['continuant'] is True
    is_sonorant = features_d[segment]['sonorant'] is True
    is_not_strident = features_d[segment]['strident'] is False or features_d[segment]['strident'] is None 
    has_lateral_feature = features_d[segment]['lateral'] is not None
    
    return is_consonantal and is_continuant and is_not_strident and is_sonorant and has_lateral_feature


def is_rothic(segment):
    is_consonantal = features_d[segment]['consonantal'] is True
    is_not_lateral = features_d[segment]['lateral'] is False
    
    return is_consonantal and is_liquid(segment) and is_not_lateral

def sanity_checks():
    plosives = 'p b t d ʈ ɖ c ɟ k ɡ q ɢ ʔ'.split()
    fricatives = 'ɸ β f v θ ð s z ʃ ʒ ʂ ʐ ç ʝ x ɣ χ ʁ ħ ʕ h ɦ'.split()
    laterals = 'l̪  l ɭ ʎ ʟ'.split()
    nasals = ' m ɱ n̪ n ɳ ɲ ŋ ɴ'.split()
    voiced = 'b d ɖ ɟ ɡ ɢ β v ð z ʒ ʐ ʝ ɣ ʁ ʕ'.split()
    voiceless = 'p t ʈ c k q ʔ ɸ f θ s ʃ ʂ ç x χ'.split()
    
    for plosive in plosives:
        assert is_plosive(plosive)
        assert not is_affricate(plosive)
        assert not is_nasal(plosive)
        assert not is_liquid(plosive)
    
    for fricative in fricatives:
        assert is_fricative(fricative)
        assert not is_affricate(fricative)
        assert not is_plosive(fricative)
        assert not is_nasal(fricative)
        assert not is_liquid(fricative)

    for lateral in laterals:
        assert is_liquid(lateral)
    
    for nasal in nasals:
        assert is_nasal(nasal)
        assert not is_fricative(nasal)
        assert not is_affricate(nasal)
        assert not is_plosive(nasal)
        assert not is_liquid(nasal)
    
    assert not is_plosive('t̠ʃ') and is_affricate('t̠ʃ')
    assert is_liquid('r')
    assert is_rothic('r')
    
    for c in voiced:
        assert is_voiced(c), c
    
    for c in voiceless:
        assert not is_voiced(c), c


In [5]:
features_d = get_features_dict('phoible-segments-features.tsv', 'phoible-phonemes.tsv')
genus_to_family = get_genus_map('family.csv', 'genus.csv')
inventories = get_inventories('phoible-aggregated.tsv', 'phoible-consonants.tsv')

# Make sure we won't make phonological errors 😉
sanity_checks()

Here we'll filter out the inventories that are possibly duplicates. The criterion will be multiple occurences of an identifier made of the language code and the language name concatenated in lower case with stripped spaces. The inventory we'll keep is the one with a PHOIBLE or SAPHON inventory preferably.

In [6]:
def get_canonical_name(inventory):
    code = inventory['LanguageCode']
    name = inventory['LanguageName']
    name = name.replace(' ', '')
    name = name.lower()
    return '{}{}'.format(code, name)


def filter_inventories(inventories):
    codes = [get_canonical_name(i) for i in inventories]
    dupes = [item for item, count in collections.Counter(codes).items() if count > 1]
    dupe_sources = {}

    for code in dupes:
        for inventory in inventories:
            inventory_id = get_canonical_name(inventory)
            if inventory_id == code:
                try:
                    dupe_sources[inventory_id].append(inventory['Source'])
                except KeyError:
                    dupe_sources[inventory_id] = [inventory['Source']]

    filtered_inventories = []
    for inventory in inventories:
        inventory_id = get_canonical_name(inventory)

        if inventory_id in dupes:
            source = inventory['Source']
            if source != 'PH' and 'PH' in dupe_sources[inventory_id]:
                continue
            elif source != 'SAPHON' and 'SAPHON' in dupe_sources[inventory_id]:
                continue
            elif source != 'UPSID' and 'UPSID' in dupe_sources[inventory_id]:
                continue
            else:
                filtered_inventories.append(inventory)
        else:
            filtered_inventories.append(inventory)

    return filtered_inventories


inventories = filter_inventories(inventories)[:160]
# aleatori: inventories = random.sample(inventories, 160)
inventories.sort(key=lambda k: k['LanguageFamilyRoot']+k['LanguageFamilyGenus'])

## Família, genus, llengua i segments

In [7]:
html_table = ['<table>']

total_segments = 0
# Build the header
html_table.append('<tr>')
for header in ['Familia', 'Genus', 'Area', 'Llengua', '#', 'Segments']:
    html_table.append('<td><b>{}</b></td>'.format(header))
else:
    html_table.append('</tr>')

# Add the actual payload
for inventory in inventories:
    html_table.append('<tr>')
    for attribute in ['LanguageFamilyRoot', 'LanguageFamilyGenus', 'Area', 'LanguageName']: 
        html_table.append('<td>{}</td>'.format(inventory[attribute]))
    else:
        html_table.append('<td>{}</td>'.format(len(inventory['Segments'])))
        total_segments += len(inventory['Segments'])
        html_table.append('<td>')
        html_table.append('  '.join(sorted(inventory['Segments'])))
        html_table.append('</font></td>')
        html_table.append('</tr>')

else:
    html_table.append('</table>')

    
print('Número de llengües: {}'.format(len(inventories)))
print('Mitjana de fonemes per llengua {}'.format(total_segments / len(inventories)))
# Construct the table and display it
html_table = ''.join(html_table)
html_table = HTML(html_table)
display(html_table)

Número de llengües: 160
Mitjana de fonemes per llengua 12.00625


Familia Genus Area Llengua # Segments Ainu Ainu Asia Ainu 11 h j k m n p s t t̠ʃ w ɾ Algic Algonquian America Shawnee 13 j k kː l m n p t t̠ʃ w ʃ ʔ θ Algic Algonquian America Blackfoot 13 h j k l m n p s t̠ʃ t̪ w x ʔ Arauan Arauan America Jamamadí 12 b d h k m n s t w ɟ ɸ ɾ Australian Northern Daly Pacific Malakmalak 14 j k l l̠ m n n̠ p r t t̠ w ŋ ɹ Australian Pama-Nyungan Pacific Bandjalang 12 b d d̠ʒ j l m n n̠ r w ŋ ɡ Australian Pama-Nyungan Pacific Dyirbal 13 b d j l m n r w ŋ ɟ ɡ ɲ ɻ Australian Pama-Nyungan Pacific Gugu-Yalandyi 13 *R̪ c j k l̪ m n̪ p t̪ w ŋ ɲ ɻ Australian Pama-Nyungan Pacific Wik-Munkan 13 j k l m n n̠ p r t t̠ w ŋ ʔ Australian Pama-Nyungan Pacific Yidiny 13 b d j l m n r w ŋ ɟ ɡ ɲ ɻ Australian Tiwian Pacific Tiwi 14 j k l m n n̪ p t t̪ w ŋ ɣ ɻ ɾ Austronesian Central Malayo-Polynesian Asia Tetun 14 b d̪ f h k l̪ m n̪ p r̪ s̪ t̪ w ʔ Austronesian Central Malayo-Polynesian Asia Southern Nuautl 12 h j k l m n p r s t w ʔ Austronesian Central Malayo-Polynesian Asia Selaru 14 b d f h j k l m n r s t w ʔ Austronesian Central Malayo-Polynesian Asia Leti 10 d k l m n p r s t β Austronesian Oceanic Pacific Maori 10 f h k m n p t w ŋ ɾ Austronesian Oceanic America Hawaiian 8 h k l̪ m n̪ p w ʔ Austronesian Oceanic Pacific Pohnpeian 14 j k l̪ m mʷ n̪ p pʷ r s t̪ w ŋ ʈʂ Austronesian Oceanic Pacific Roro 9 b h k m n̪ p t̪ ɾ̪ ʔ Austronesian Oceanic Pacific Tigak 12 b k m n p r s t ŋ ɡ ɮ β Austronesian Oceanic Pacific Manam 13 b d k l m n p s t z ŋ ɡ ɾ Austronesian Oceanic Pacific Seimat 11 h k l m n p s t̪ w x ŋ Austronesian Oceanic Pacific Tongan; Tonga 12 f h k m n̪ p s t̪ v ŋ ɺ ʔ Austronesian Oceanic Pacific Tinputz 12 h j k l m n p s t w ʔ β Austronesian Oceanic Pacific Bariai 12 b d k l m n p r s t ŋ ɡ Austronesian Oceanic Pacific North Marquesan 12 f h k m n p r s t v ç ʔ Austronesian Palauan Pacific Palauan 10 b d̪ k l m r s t̪ ŋ ʔ Austronesian South Halmahera - West New Guinea Asia Irarutu 12 k m mb n̪ n̪d̪ s̪ t̪ w ŋɡ ɸ ɾ̪ ʝ Austronesian South Halmahera - West New Guinea Asia Biak 14 b d f j k l m n p r s t w β Baining-Taulil Baining Pacific Baining 14 k l m mb n nd p s t w ŋ ŋɡ ɣ ɾ Barbacoan Barbacoan America Awa Pit 14 j k l m n p s t̪ w z ŋ ɬ ʃ ʒ Border Border Pacific Waris 13 *R̪ j k l̪ mb n̪d̪ p s̪ t̪ w x ŋɡ β Border Border Pacific Imonda 13 b d f h k l m n p r s t ɡ Border Border Pacific Amanab 14 b f h j k m n p r s t w ŋ ɡ Cacua-Nukak Cacua-Nukak America Cacua 12 h k l m n p t t̠ʃ w ŋ ʍ ʔ Cacua-Nukak Cacua-Nukak America Nukak 12 b c d h k p t w ɟ ɡ ɾ ʔ Cahuapanan Cahuapanan America Shawi 14 h j k m n p s t t̠ʃ w ɾ ʃ ʔ β Cariban Cariban America Akawaio 13 *R̪ b d̪ j k m n̪ p s̪ t̪ w z̪ ɡ Cariban Cariban America Akurio 10 j k m n p t t̠ʃ w ɾ ʔ Cariban Cariban America Apalaí 12 j k m n p s t w z ɾ ʃ ʔ Cariban Cariban America Arára, Pará 11 j k l m n p t t̠ʃ w ŋ ɾ Cariban Cariban America Carijona 14 b d d̠ʒ h k m n s t t̠ʃ w ɡ ɲ ɾ Cariban Cariban America Ikpeng 12 j k l m n p t t̠ʃ w ŋ ɡ ɾ Cariban Cariban America Ingarikó 10 j k m n p s t w ɾ ʔ Cariban Cariban America Kaxuiâna 12 h j k m n p s t t̠ʃ w ɾ ʔ Cariban Cariban America Kuikúro-Kalapálo 14 dʲ h k l m n p s t ts w ŋ ɣ ɲ Cariban Cariban America Macushi 10 j k m n p s t w ɾ ʔ Cariban Cariban America Mapoyo 12 h j k m n p s t w ɲ ɾ ʔ Cariban Cariban America Yekwana 12 h j k m n s t t̠ʃ w ɲ ɾ ʔ Cariban Cariban America Pémono 12 h j k m n p s t w ɲ ɾ ʔ Cariban Cariban America Trió 10 h j k m n p s t w ɾ Cariban Cariban America Waiwai 14 h j k m n s t t̠ʃ w ɲ ɸ ɺ ɾ ʃ Cariban Cariban America Yabarana 11 h j k m n p s t w ɲ ɾ Chapacura-Wanham Chapacura-Wanham America Wari; Wari'; Wariʔ; Oro Nao 14 h hʷ k kʷ m mˀ n nˀ p t̠ʃ t̺ w ɾ ʔ Chapacura-Wanham Chapacura-Wanham America Oro Win 12 j k m n p s t t̪ʙ w ɾ ʔ β Chibchan Motilon America Barí 10 b d h k m n r s t ɲ Chiquito Chiquito America Bésɨro 14 c k m n p s t t̠ʃ ɲ ɾ ʂ ʃ ʔ β East Bougainville East Bougainville Pacific Nasioi 8 b k m n̪ p t̪ ɾ̪ ʔ East Strickland East Strickland Pacific Samo 12 b

In [8]:
inventories.sort(key=lambda k: k['LanguageName'])

## Sistemes secundaris

In [9]:
sistemes_secundaris = [
'Awtu, Aspiració',
'Auyana, Allargament',
'Comanche, Labialització',
'Dadibi, Aspiració',
'Dani, Labialització',
'ekari, Alliberament lateral',
'fuzhou, Aspiració',
'gaviao do para, Aspiració',
'guajajara, Labialització',
'kayabi, Labialització',
'kitsijis, Aspiració',
'karajo, Aspiració',
'krinkati-tinbira, Aspiració',
'kuikura-kalapalo, Palatalització',
'northern paiute, Labialització',
'pompeian, Labialització',
'sanuma, Aspiració',
'shawnee, Llargada',
'shirihana, Aspiració',
'wantoat, Labialització',
'wariwari, Labialització / Glotalitzacio',
'yawa, Palatalització']

langs_with_aspiration = 0
langs_with_labialitzation = 0
langs_with_palatalitzation = 0
langs_with_glotalization = 0
langs_with_duration = 0
langs_with_lateralrelease = 0

html_table = ['<table>']
html_table.append('<tr><td>Llengua</td><td>Sistema secundari</td>')

for s in sistemes_secundaris:
    if 'Labialització' in s:
        langs_with_labialitzation += 1
    if 'Aspiració' in s:
        langs_with_aspiration += 1
    if 'Palatalitzaci' in s:
        langs_with_palatalitzation += 1
    if 'Llargada' in s:
        langs_with_duration += 1
    if 'Glotalitzacio' in s:
        langs_with_glotalization += 1
    if 'Alliberament' in s:
        langs_with_lateralrelease += 1

    html_table.append('<tr>')
    for attr in s.split(','):
        html_table.append('<td>{}</td>'.format(attr.title()))
    
else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))

print('Labialitzacio: {} {:.2%}'.format(langs_with_labialitzation, langs_with_labialitzation / len(inventories)))
print('Aspiracio: {} {:.2%}'.format(langs_with_aspiration, langs_with_aspiration / len(inventories)))
print('Palatalitzacio: {} {:.2%}'.format(langs_with_palatalitzation, langs_with_palatalitzation / len(inventories)))
print('Duracio: {} {:.2%}'.format(langs_with_duration, langs_with_duration / len(inventories)))
print('Glotalitzacio: {} {:.2%}'.format(langs_with_glotalization, langs_with_glotalization / len(inventories)))
print('Alliberament lateral: {} {:.2%}'.format(langs_with_lateralrelease, langs_with_lateralrelease / len(inventories)))

Llengua Sistema secundari Awtu Aspiració Auyana Allargament Comanche Labialització Dadibi Aspiració Dani Labialització Ekari Alliberament Lateral Fuzhou Aspiració Gaviao Do Para Aspiració Guajajara Labialització Kayabi Labialització Kitsijis Aspiració Karajo Aspiració Krinkati-Tinbira Aspiració Kuikura-Kalapalo Palatalització Northern Paiute Labialització Pompeian Labialització Sanuma Aspiració Shawnee Llargada Shirihana Aspiració Wantoat Labialització Wariwari Labialització / Glotalitzacio Yawa Palatalització

Labialitzacio: 8 5.00%
Aspiracio: 9 5.62%
Palatalitzacio: 2 1.25%
Duracio: 1 0.62%
Glotalitzacio: 1 0.62%
Alliberament lateral: 1 0.62%


## Presència de fonemes

In [10]:
all_consonants = []
for inventory in inventories:
    for consonant in inventory['Segments']:
        all_consonants.append(consonant)

all_consonants = sorted(all_consonants)
all_consonants_count = []
counted = []
for consonant in all_consonants:
    if consonant not in counted:
        counted.append(consonant)
        count = all_consonants.count(consonant)
        all_consonants_count.append([consonant, count,
                                     '{:.2%}'.format(count / len(inventories))])

all_consonants_count.sort(key=lambda f: f[1], reverse=True)
all_consonants_uniq = [c[0] for c in all_consonants_count]

html_table = ['<table>']
html_table.append('<tr><td>Fonema</td><td>Ocurrències</td><td>Percentatge</td></tr>')

for consonant in all_consonants_count:
    html_table.append('<tr>')
    for attribute in consonant:
        html_table.append('<td>{}</td>'.format(attribute))
    
    html_table.append('</tr>')
else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))

Fonema Ocurrències Percentatge k 151 94.38% m 143 89.38% p 132 82.50% w 125 78.12% n 117 73.12% t 114 71.25% j 108 67.50% s 88 55.00% h 82 51.25% b 59 36.88% ɾ 59 36.88% ʔ 58 36.25% ŋ 53 33.12% l 49 30.63% d 47 29.38% t̠ʃ 43 26.88% ɡ 42 26.25% t̪ 37 23.12% r 28 17.50% ɲ 28 17.50% n̪ 26 16.25% f 25 15.62% s̪ 21 13.12% β 18 11.25% ʃ 14 8.75% d̪ 11 6.88% x 11 6.88% ɸ 11 6.88% c 10 6.25% l̪ 10 6.25% ts 10 6.25% d̠ʒ 9 5.62% kʷ 8 5.00% mb 8 5.00% ŋɡ 8 5.00% kʰ 7 4.38% ɾ̪ 7 4.38% *R̪ 6 3.75% ɟ 6 3.75% ɣ 6 3.75% dz 5 3.12% v 5 3.12% z 5 3.12% kp 4 2.50% nd 4 2.50% n̠ 4 2.50% n̪d̪ 4 2.50% tʰ 4 2.50% ɻ 4 2.50% θ 4 2.50% pʰ 3 1.88% r̪ 3 1.88% ð 3 1.88% ɺ 3 1.88% ʒ 3 1.88% cç 2 1.25% d̠ 2 1.25% d̪z̪ 2 1.25% t̠ 2 1.25% t̪s̪ 2 1.25% t̪ʰ 2 1.25% ç 2 1.25% ŋʷ 2 1.25% ɗ 2 1.25% ɹ 2 1.25% ɺ̪ 2 1.25% ɽ 2 1.25% ʂ 2 1.25% ʝ 2 1.25% *R 1 0.62% bv 1 0.62% bz 1 0.62% dʲ 1 0.62% hʷ 1 0.62% kː 1 0.62% l̠ 1 0.62% mʷ 1 0.62% mˀ 1 0.62% mː 1 0.62% nʲ 1 0.62% nˀ 1 0.62% nː 1 0.62% n̠d̠ʒ 1 0.62% n̪z̪ 1 0.62% ps 1 0.62% pʷ 1 0.62% sʲ 1 0.62% ts͇ 1 0.62% t̪s̪ʰ 1 0.62% t̪ʙ 1 0.62% t̺ 1 0.62% z̪ 1 0.62% ŋɡʷ 1 0.62% ɓ 1 0.62% ɟʝ 1 0.62% ɡb 1 0.62% ɡˡ 1 0.62% ɥ 1 0.62% ɦ 1 0.62% ɬ 1 0.62% ɬ̪ 1 0.62% ɭ͓ 1 0.62% ɮ 1 0.62% ɰ 1 0.62% ɲɟ 1 0.62% ʈʂ 1 0.62% ʍ 1 0.62% ʟ 1 0.62% ᴅ 1 0.62%

In [11]:
print(len(all_consonants_uniq))

109


* hem de mirar obstruents, quantes d'elles són sordes i sonores
* de les obstruents quantes oclusives i sordes i sonores
* presència d'africades i les seves qualitats
* nasals

## Obstruents

In [12]:
langs_with_obstruents = []
for inventory in inventories:
    obstruents_voiced = []
    obstruents_voiceless = []

    for segment in inventory['Segments']:
        if features_d[segment]['sonorant'] is False:
            if is_voiced(segment):
                obstruents_voiced.append(segment)
            else:
                obstruents_voiceless.append(segment)

    else:
        langs_with_obstruents.append({inventory['LanguageName']: [obstruents_voiced, obstruents_voiceless]})

html_table = ['<font face="Doulos SIL" size=4em><table>']
html_table.append('<tr><td>Llengua</td><td>obstruents sonores</td><td>obstruents sordes</td><td>total (sonores + sordes)</td>')
for lang in langs_with_obstruents:
    for inv in lang:
        voiced_inv = lang[inv][0]
        voiceless_inv = lang[inv][1]
        joined_inv = list(voiced_inv + voiceless_inv)
        
        html_table.append('<tr>')
        html_table.append('<td>{}</td>'.format(inv))
        html_table.append('<td>{}</td>'.format(' '.join(voiced_inv)))
        html_table.append('<td>{}</td>'.format(' '.join(voiceless_inv)))
        html_table.append('<td>{}</td>'.format("{} ({} + {})".format(len(joined_inv),
                                                                     len(voiced_inv),
                                                                     len(voiceless_inv))))

        #for item in sorted(lang[inv]):
        #    html_table.append('<td>{}</td>'.format(item))
        html_table.append('</tr>')
else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))

Llengua obstruents sonores obstruents sordes total (sonores + sordes) Abau h k p s 4 (0 + 4) Ache β d̠ʒ t̠ʃ k p t̪ 6 (2 + 4) Aguaruna ʃ h k ts p s t t̠ʃ ʔ 9 (0 + 9) Ainu h k p s t̠ʃ t 6 (0 + 6) Akawaio d̪ z̪ ɡ b s̪ k p t̪ 8 (4 + 4) Akurio ʔ t̠ʃ k p t 5 (0 + 5) Alabama b k ɬ̪ p s t̪ h ɸ t̠ʃ 9 (1 + 8) Amahuaca ʔ s̪ t̠ʃ θ h k p t̪ x 9 (0 + 9) Amanab ɡ b h k f p s t 8 (2 + 6) Angaatiha ʔ k p t̠ʃ t 5 (0 + 5) Ao ɭ͓ z cç k p s t ʔ 8 (2 + 6) Apalaí z ʃ k p s t ʔ 7 (1 + 6) Apinaye ʒ v ʔ s̪ k p t̠ʃ t 8 (2 + 6) Arabela ʃ s̪ h k p t̪ 6 (0 + 6) Arára, Pará k p t̠ʃ t 4 (0 + 4) Arikapú t̠ʃ h k p t ʔ 6 (0 + 6) Asmat ʝ f k p s t̠ʃ t 7 (1 + 6) Au ɣ k p s t 5 (1 + 4) Auca ɡ b d k p t 6 (3 + 3) Auyana ʔ k p t 4 (0 + 4) Awa Pit ʒ z ʃ ɬ k p s t̪ 8 (2 + 6) Awtuw d pʰ tʰ kʰ 4 (1 + 3) Baining ɣ k p s t 5 (1 + 4) Bandjalang ɡ b d d̠ʒ 4 (4 + 0) Barasano ɡ b d k p s t h 8 (3 + 5) Bariai ɡ b d k p s t 7 (3 + 4) Barí b d h k s t 6 (2 + 4) Baruga β d̠ʒ ɡ ɣ b d k s t ɸ 10 (6 + 4) Bésɨro β ʃ ʂ t̠ʃ c k p s t ʔ 10 (1 + 9) Biak β b d f k p s t 8 (3 + 5) Biali b d k f p s t h 8 (2 + 6) Biloxi d c p h k s t x 8 (1 + 7) Binandere β ɡ b d k p t 7 (4 + 3) Binumarien k t p s ʔ ɸ 6 (0 + 6) Blackfoot ʔ t̪ t̠ʃ h k p s x 8 (0 + 8) Bororo ɡ b d̪ d̠ʒ p t̪ t̠ʃ k 8 (4 + 4) Cacua ʍ ʔ k p t̠ʃ t h 7 (0 + 7) Canela ʔ t̠ʃ h k p t 6 (0 + 6) Carijona d̠ʒ ɡ b d t̠ʃ h k s t 9 (4 + 5) Cherokee ɡ d dz ʃ h ʔ 6 (3 + 3) Chuave ɡ b d f k s t 7 (3 + 4) Comanche h k p s t̪ ʔ kʷ t̪s̪ 8 (0 + 8) Crow ʃ s̪ t̠ʃ t̪ h k p x 8 (0 + 8) Cubeo d̠ β b d ð p x k t̠ʃ t 10 (5 + 5) Dadibi kʰ pʰ h k tʰ p s t 8 (0 + 8) Dani ʔ s̪ kʷ h k p t̪ 7 (0 + 7) Dera ɡ b d̪ k p t̪ 6 (3 + 3) Dyirbal ɡ b ɟ d 4 (4 + 0) Efik b d f k s kp t 7 (2 + 5) Ekari ɡˡ b d k p t 6 (3 + 3) Endo c k p s t 5 (0 + 5) Faiwol ɡ b d f k s t 7 (3 + 4) Fasu ɸ h k p s t 6 (0 + 6) Fuzhou s̪ kʰ t̪ t̪ʰ t̪s̪ pʰ k p x t̪s̪ʰ 10 (0 + 10) Gadsup d β k t p ʔ 6 (2 + 4) Gavião do Pará kʰ t̠ʃ h k p t 6 (0 + 6) Golin ɡ b d k p s t 7 (3 + 4) Guajajara z ʔ ts kʷ t̪ h k p 8 (1 + 7) Gugu-Yalandyi c k p t̪ 4 (0 + 4) Hawaiian k p ʔ h 4 (0 + 4) Huron h k s x ʔ θ t 7 (0 + 7) Ikpeng ɡ k p t t̠ʃ 5 (1 + 4) Imonda ɡ b d f h k p s t 9 (3 + 6) Ingarikó k p s t ʔ 5 (0 + 5) Irarutu ʝ k s̪ t̪ ɸ 5 (1 + 4) Isaka b d k p s t ɸ 7 (2 + 5) Iwam h p s t k 5 (0 + 5) Jabutí β d̠ʒ bz ps t̠ʃ h k p t 9 (3 + 6) Jamamadí b d ɟ h k s t ɸ 8 (3 + 5) Kaiabi ɡ ʔ kʷ k p s t ɸ 8 (1 + 7) Karajá ɗ b d θ h k 6 (3 + 3) Karitiana; Karitiâna k p s t h 5 (0 + 5) Katukína b d d̠ʒ h k p t̠ʃ t 8 (3 + 5) Kaxuiâna h k p s t t̠ʃ ʔ 7 (0 + 7) Kikamba β ð k s t 5 (2 + 3) Kipsigis tʰ kʰ t̠ʃ ç h p s 7 (0 + 7) Klao ɡb d̪ ɟʝ b cç s̪ t̪ f p kp 10 (4 + 6) Koiari ɡ b d ð f h k t 8 (4 + 4) Kokama-Kokamilla k ts p x t̠ʃ t 6 (0 + 6) Krahô ts kʰ h k p t 6 (0 + 6) Krinkati-Timbira kʰ t̠ʃ h k p t 6 (0 + 6) Kuikúro-Kalapálo dʲ ɣ ts h k p s t 8 (2 + 6) Kuot ɡ b d f k p s t 8 (3 + 5) Leti β d k p s t 6 (2 + 4) Macushi ʔ k p s t 5 (0 + 5) Malakmalak k p t t̠ 4 (0 + 4) Manam ɡ b d z p k s t 8 (4 + 4) Maori f h k p t 5 (0 + 5) Mapoyo h k p s t ʔ 6 (0 + 6) Maxakali k p t̠ʃ t h ʔ 6 (0 + 6) Mianmin ɡ b d f h k s t 8 (3 + 5) Mixe d̪ ʒ ɡ v ʃ ts͇ ʔ s̪ k p t̪ 11 (4 + 7) Namia k p t 3 (0 + 3) Nandi c k p s t 5 (0 + 5) Nankina ɡ b d β dz k ts p t 9 (5 + 4) Nasioi b p k t̪ ʔ 5 (1 + 4) Nateni ɟ b d c f h k p s kp t 11 (3 + 8) Ngomba ɡ bv dz d k p t 7 (4 + 3) Nimboran ɡ b d̪ s̪ k p t̪ h 8 (3 + 5) Ningil ɡ ʔ k p s t ɸ 7 (1 + 6) North Marquesan v ʔ ç f h k p s t 9 (1 + 8) Northern Paiute ʔ ts kʷ t̠ʃ h p s t k 9 (0 + 9) Nukak ɟ ɡ b d ʔ c h k p t 10 (4 + 6) Nɔmaa (NɔmaáNdɛ́) c f k p s t h 7 (0 + 7) Oneida ʔ h k s t̠ʃ t 6 (0 + 6) Oro Win β k p s t ʔ 6 (1 + 5) Orokaiva ɡ b d dz h k p s t 9 (4 + 5) Palauan d̪ b ʔ t̪ k s 6 (2 + 4) Panará h k p s t ʔ 6 (0 + 6) Pémono h p s t k ʔ 6 (0 + 6) Piraha ɡ b s̪ k p t̪ ʔ h 8 (2 + 6) Pohnpeian pʷ k p s t̪ ʈʂ 6 (0 + 6) Puinave h k p s ʔ t 6 (0 + 6) Rikbaktsa b d ʃ t̠ʃ h k p t 8 (2 + 6) Roro b h k p t̪ ʔ 6 (1 + 5) Rotokas ɡ β k p t 5 (2 + 3) Sabane ɗ ɓ k s p h ʔ t 8 (2 + 6) Sabaot b k s t̠ʃ t 

## Oclusives

In [13]:
langs_with_plosives = []
more_voiceless_plosives = 0
for inventory in inventories:
    plosives_voiced = []
    plosives_voiceless = []

    for segment in inventory['Segments']:
        if is_plosive(segment):
            if is_voiced(segment):
                plosives_voiced.append(segment)
            else:
                plosives_voiceless.append(segment)

    else:
        langs_with_plosives.append({inventory['LanguageName']: [plosives_voiced, plosives_voiceless]})

html_table = ['<table>']
html_table.append('<tr><td>Llengua</td><td>plosives sonores</td><td>plosives sordes</td><td>total (sonores + sordes)</td>')
for lang in langs_with_plosives:
    for inv in lang:
        voiced_inv = lang[inv][0]
        voiceless_inv = lang[inv][1]
        joined_inv = list(voiced_inv + voiceless_inv)
        
        if len(voiceless_inv) > len(voiced_inv):
            more_voiceless_plosives += 1
        
        html_table.append('<tr>')
        html_table.append('<td>{}</td>'.format(inv))
        html_table.append('<td>{}</td>'.format(' '.join(voiced_inv)))
        html_table.append('<td>{}</td>'.format(' '.join(voiceless_inv)))
        html_table.append('<td>{}</td>'.format("{} ({} + {})".format(len(joined_inv),
                                                                     len(voiced_inv),
                                                                     len(voiceless_inv))))

        #for item in sorted(lang[inv]):
        #    html_table.append('<td>{}</td>'.format(item))
        html_table.append('</tr>')
else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))

print('El nombre d’oclusives sordes és normalment major o igual al d’oclusives sonores: {:.2%} ({} / {})'.format(more_voiceless_plosives / len(langs_with_plosives),
                                           more_voiceless_plosives, len(langs_with_plosives)))

Llengua plosives sonores plosives sordes total (sonores + sordes) Abau k p 2 (0 + 2) Ache k p t̪ 3 (0 + 3) Aguaruna k p t ʔ 4 (0 + 4) Ainu k p t 3 (0 + 3) Akawaio d̪ ɡ b k p t̪ 6 (3 + 3) Akurio ʔ k p t 4 (0 + 4) Alabama b k p t̪ 4 (1 + 3) Amahuaca ʔ k p t̪ 4 (0 + 4) Amanab ɡ b k p t 5 (2 + 3) Angaatiha ʔ k p t 4 (0 + 4) Ao k p t ʔ 4 (0 + 4) Apalaí k p t ʔ 4 (0 + 4) Apinaye ʔ k p t 4 (0 + 4) Arabela k p t̪ 3 (0 + 3) Arára, Pará k p t 3 (0 + 3) Arikapú k p t ʔ 4 (0 + 4) Asmat k p t 3 (0 + 3) Au k p t 3 (0 + 3) Auca ɡ b d k p t 6 (3 + 3) Auyana ʔ k p t 4 (0 + 4) Awa Pit k p t̪ 3 (0 + 3) Awtuw d pʰ tʰ kʰ 4 (1 + 3) Baining k p t 3 (0 + 3) Bandjalang ɡ b d 3 (3 + 0) Barasano ɡ b d k p t 6 (3 + 3) Bariai ɡ b d k p t 6 (3 + 3) Barí b d k t 4 (2 + 2) Baruga ɡ b d k t 5 (3 + 2) Bésɨro c k p t ʔ 5 (0 + 5) Biak b d k p t 5 (2 + 3) Biali b d k p t 5 (2 + 3) Biloxi d c p k t 5 (1 + 4) Binandere ɡ b d k p t 6 (3 + 3) Binumarien k t p ʔ 4 (0 + 4) Blackfoot ʔ t̪ k p 4 (0 + 4) Bororo ɡ b d̪ p t̪ k 6 (3 + 3) Cacua ʔ k p t 4 (0 + 4) Canela ʔ k p t 4 (0 + 4) Carijona ɡ b d k t 5 (3 + 2) Cherokee ɡ d ʔ 3 (2 + 1) Chuave ɡ b d k t 5 (3 + 2) Comanche k p t̪ ʔ kʷ 5 (0 + 5) Crow t̪ k p 3 (0 + 3) Cubeo d̠ b d p k t 6 (3 + 3) Dadibi kʰ pʰ k tʰ p t 6 (0 + 6) Dani ʔ kʷ k p t̪ 5 (0 + 5) Dera ɡ b d̪ k p t̪ 6 (3 + 3) Dyirbal ɡ b ɟ d 4 (4 + 0) Efik b d k kp t 5 (2 + 3) Ekari ɡˡ b d k p t 6 (3 + 3) Endo c k p t 4 (0 + 4) Faiwol ɡ b d k t 5 (3 + 2) Fasu k p t 3 (0 + 3) Fuzhou kʰ t̪ t̪ʰ pʰ k p 6 (0 + 6) Gadsup d k t p ʔ 5 (1 + 4) Gavião do Pará kʰ k p t 4 (0 + 4) Golin ɡ b d k p t 6 (3 + 3) Guajajara ʔ kʷ t̪ k p 5 (0 + 5) Gugu-Yalandyi c k p t̪ 4 (0 + 4) Hawaiian k p ʔ 3 (0 + 3) Huron k ʔ t 3 (0 + 3) Ikpeng ɡ k p t 4 (1 + 3) Imonda ɡ b d k p t 6 (3 + 3) Ingarikó k p t ʔ 4 (0 + 4) Irarutu k t̪ 2 (0 + 2) Isaka b d k p t 5 (2 + 3) Iwam p t k 3 (0 + 3) Jabutí k p t 3 (0 + 3) Jamamadí b d ɟ k t 5 (3 + 2) Kaiabi ɡ ʔ kʷ k p t 6 (1 + 5) Karajá ɗ b d k 4 (3 + 1) Karitiana; Karitiâna k p t 3 (0 + 3) Katukína b d k p t 5 (2 + 3) Kaxuiâna k p t ʔ 4 (0 + 4) Kikamba k t 2 (0 + 2) Kipsigis tʰ kʰ p 3 (0 + 3) Klao ɡb d̪ b t̪ p kp 6 (3 + 3) Koiari ɡ b d k t 5 (3 + 2) Kokama-Kokamilla k p t 3 (0 + 3) Krahô kʰ k p t 4 (0 + 4) Krinkati-Timbira kʰ k p t 4 (0 + 4) Kuikúro-Kalapálo dʲ k p t 4 (1 + 3) Kuot ɡ b d k p t 6 (3 + 3) Leti d k p t 4 (1 + 3) Macushi ʔ k p t 4 (0 + 4) Malakmalak k p t t̠ 4 (0 + 4) Manam ɡ b d p k t 6 (3 + 3) Maori k p t 3 (0 + 3) Mapoyo k p t ʔ 4 (0 + 4) Maxakali k p t ʔ 4 (0 + 4) Mianmin ɡ b d k t 5 (3 + 2) Mixe d̪ ɡ ʔ k p t̪ 6 (2 + 4) Namia k p t 3 (0 + 3) Nandi c k p t 4 (0 + 4) Nankina ɡ b d k p t 6 (3 + 3) Nasioi b p k t̪ ʔ 5 (1 + 4) Nateni ɟ b d c k p kp t 8 (3 + 5) Ngomba ɡ d k p t 5 (2 + 3) Nimboran ɡ b d̪ k p t̪ 6 (3 + 3) Ningil ɡ ʔ k p t 5 (1 + 4) North Marquesan ʔ k p t 4 (0 + 4) Northern Paiute ʔ kʷ p t k 5 (0 + 5) Nukak ɟ ɡ b d ʔ c k p t 9 (4 + 5) Nɔmaa (NɔmaáNdɛ́) c k p t 4 (0 + 4) Oneida ʔ k t 3 (0 + 3) Oro Win k p t ʔ 4 (0 + 4) Orokaiva ɡ b d k p t 6 (3 + 3) Palauan d̪ b ʔ t̪ k 5 (2 + 3) Panará k p t ʔ 4 (0 + 4) Pémono p t k ʔ 4 (0 + 4) Piraha ɡ b k p t̪ ʔ 6 (2 + 4) Pohnpeian pʷ k p t̪ 4 (0 + 4) Puinave k p ʔ t 4 (0 + 4) Rikbaktsa b d k p t 5 (2 + 3) Roro b k p t̪ ʔ 5 (1 + 4) Rotokas ɡ k p t 4 (1 + 3) Sabane ɗ ɓ k p ʔ t 6 (2 + 4) Sabaot b k t 3 (1 + 2) Samo ɡ b d k t 5 (3 + 2) Sanuma; Sanumá tʰ k p t 4 (0 + 4) Sebei c p t̪ k 4 (0 + 4) Seimat t̪ k p 3 (0 + 3) Selaru b d k t ʔ 5 (2 + 3) Seneca b k t̪ ʔ 4 (1 + 3) Sentani d̪ k p t̪ 4 (1 + 3) Shanenawa k p t 3 (0 + 3) Shawi k p ʔ t 4 (0 + 4) Shawnee p k kː t ʔ 5 (0 + 5) Shiriana t̪ʰ k p t̪ 4 (0 + 4) Shuar k p t 3 (0 + 3) Skou ɟ b k p t 5 (2 + 3) Southern Kiwai ɡ b d̪ k p t̪ ʔ 7 (3 + 4) Southern Nuautl k p t ʔ 4 (0 + 4) Suena ɡ b d̪ k p t̪ 6 (3 + 3) Suyá k p t 3 (0 + 3) Taoripi k p t̪ 3 (0 + 3) Taushiro k kʷ ʔ t 4 (0 + 4) Tetun b d̪ k p t̪ ʔ 6 (2 + 4) Tigak ɡ b p k t 5 (2 + 3) Tinputz ʔ k p t 4 (0 + 4) Tiwi k p t̪ t 4 (0 + 4) Tongan; Tonga k p t̪ ʔ 4 (0 + 4) Trió k p t 3 (0 + 3) U

El nombre d’oclusives sordes és normalment major o igual al d’oclusives sonores: 77.50% (124 / 160)


## Fricatives

In [14]:
langs_with_fricatives = []
for inventory in inventories:
    fricatives_voiced = []
    fricatives_voiceless = []

    for segment in inventory['Segments']:
        if is_fricative(segment):
            if is_voiced(segment):
                fricatives_voiced.append(segment)
            else:
                fricatives_voiceless.append(segment)

    else:
        langs_with_fricatives.append({inventory['LanguageName']: [fricatives_voiced, fricatives_voiceless]})

html_table = ['<font face="Doulos SIL" size=4em><table>']
html_table.append('<tr><td>Llengua</td><td>fricatives sonores</td><td>fricatives sordes</td><td>total (sonores + sordes)</td>')
for lang in langs_with_fricatives:
    for inv in lang:
        voiced_inv = lang[inv][0]
        voiceless_inv = lang[inv][1]
        joined_inv = list(voiced_inv + voiceless_inv)
        
        html_table.append('<tr>')
        html_table.append('<td>{}</td>'.format(inv))
        html_table.append('<td>{}</td>'.format(' '.join(voiced_inv)))
        html_table.append('<td>{}</td>'.format(' '.join(voiceless_inv)))
        html_table.append('<td>{}</td>'.format("{} ({} + {})".format(len(joined_inv),
                                                                     len(voiced_inv),
                                                                     len(voiceless_inv))))

        #for item in sorted(lang[inv]):
        #    html_table.append('<td>{}</td>'.format(item))
        html_table.append('</tr>')
else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))

Llengua fricatives sonores fricatives sordes total (sonores + sordes) Abau h s 2 (0 + 2) Ache β 1 (1 + 0) Aguaruna ʃ h s 3 (0 + 3) Ainu h s 2 (0 + 2) Akawaio z̪ s̪ 2 (1 + 1) Akurio 0 (0 + 0) Alabama ɬ̪ s h ɸ 4 (0 + 4) Amahuaca s̪ θ h x 4 (0 + 4) Amanab h f s 3 (0 + 3) Angaatiha 0 (0 + 0) Ao ɭ͓ z s 3 (2 + 1) Apalaí z ʃ s 3 (1 + 2) Apinaye ʒ v s̪ 3 (2 + 1) Arabela ʃ s̪ h 3 (0 + 3) Arára, Pará 0 (0 + 0) Arikapú h 1 (0 + 1) Asmat ʝ f s 3 (1 + 2) Au ɣ s 2 (1 + 1) Auca 0 (0 + 0) Auyana 0 (0 + 0) Awa Pit ʒ z ʃ ɬ s 5 (2 + 3) Awtuw 0 (0 + 0) Baining ɣ s 2 (1 + 1) Bandjalang 0 (0 + 0) Barasano s h 2 (0 + 2) Bariai s 1 (0 + 1) Barí h s 2 (0 + 2) Baruga β ɣ s ɸ 4 (2 + 2) Bésɨro β ʃ ʂ s 4 (1 + 3) Biak β f s 3 (1 + 2) Biali f s h 3 (0 + 3) Biloxi h s x 3 (0 + 3) Binandere β 1 (1 + 0) Binumarien s ɸ 2 (0 + 2) Blackfoot h s x 3 (0 + 3) Bororo 0 (0 + 0) Cacua ʍ h 2 (0 + 2) Canela h 1 (0 + 1) Carijona h s 2 (0 + 2) Cherokee ʃ h 2 (0 + 2) Chuave f s 2 (0 + 2) Comanche h s 2 (0 + 2) Crow ʃ s̪ h x 4 (0 + 4) Cubeo β ð x 3 (2 + 1) Dadibi h s 2 (0 + 2) Dani s̪ h 2 (0 + 2) Dera 0 (0 + 0) Dyirbal 0 (0 + 0) Efik f s 2 (0 + 2) Ekari 0 (0 + 0) Endo s 1 (0 + 1) Faiwol f s 2 (0 + 2) Fasu ɸ h s 3 (0 + 3) Fuzhou s̪ x 2 (0 + 2) Gadsup β 1 (1 + 0) Gavião do Pará h 1 (0 + 1) Golin s 1 (0 + 1) Guajajara z h 2 (1 + 1) Gugu-Yalandyi 0 (0 + 0) Hawaiian h 1 (0 + 1) Huron h s x θ 4 (0 + 4) Ikpeng 0 (0 + 0) Imonda f h s 3 (0 + 3) Ingarikó s 1 (0 + 1) Irarutu ʝ s̪ ɸ 3 (1 + 2) Isaka s ɸ 2 (0 + 2) Iwam h s 2 (0 + 2) Jabutí β bz ps h 4 (2 + 2) Jamamadí h s ɸ 3 (0 + 3) Kaiabi s ɸ 2 (0 + 2) Karajá θ h 2 (0 + 2) Karitiana; Karitiâna s h 2 (0 + 2) Katukína h 1 (0 + 1) Kaxuiâna h s 2 (0 + 2) Kikamba β ð s 3 (2 + 1) Kipsigis ç h s 3 (0 + 3) Klao s̪ f 2 (0 + 2) Koiari ð f h 3 (1 + 2) Kokama-Kokamilla x 1 (0 + 1) Krahô h 1 (0 + 1) Krinkati-Timbira h 1 (0 + 1) Kuikúro-Kalapálo ɣ h s 3 (1 + 2) Kuot f s 2 (0 + 2) Leti β s 2 (1 + 1) Macushi s 1 (0 + 1) Malakmalak 0 (0 + 0) Manam z s 2 (1 + 1) Maori f h 2 (0 + 2) Mapoyo h s 2 (0 + 2) Maxakali h 1 (0 + 1) Mianmin f h s 3 (0 + 3) Mixe ʒ v ʃ s̪ 4 (2 + 2) Namia 0 (0 + 0) Nandi s 1 (0 + 1) Nankina β 1 (1 + 0) Nasioi 0 (0 + 0) Nateni f h s 3 (0 + 3) Ngomba 0 (0 + 0) Nimboran s̪ h 2 (0 + 2) Ningil s ɸ 2 (0 + 2) North Marquesan v ç f h s 5 (1 + 4) Northern Paiute h s 2 (0 + 2) Nukak h 1 (0 + 1) Nɔmaa (NɔmaáNdɛ́) f s h 3 (0 + 3) Oneida h s 2 (0 + 2) Oro Win β s 2 (1 + 1) Orokaiva h s 2 (0 + 2) Palauan s 1 (0 + 1) Panará h s 2 (0 + 2) Pémono h s 2 (0 + 2) Piraha s̪ h 2 (0 + 2) Pohnpeian s 1 (0 + 1) Puinave h s 2 (0 + 2) Rikbaktsa ʃ h 2 (0 + 2) Roro h 1 (0 + 1) Rotokas β 1 (1 + 0) Sabane s h 2 (0 + 2) Sabaot s 1 (0 + 1) Samo f h s 3 (0 + 3) Sanuma; Sanumá h s 2 (0 + 2) Sebei s̪ 1 (0 + 1) Seimat h s x 3 (0 + 3) Selaru f s h 3 (0 + 3) Seneca h s̪ 2 (0 + 2) Sentani f h 2 (0 + 2) Shanenawa ʂ f h s 4 (0 + 4) Shawi β ʃ h s 4 (1 + 3) Shawnee ʃ θ 2 (0 + 2) Shiriana ʃ s̪ h 3 (0 + 3) Shuar ʃ s h 3 (0 + 3) Skou f h 2 (0 + 2) Southern Kiwai s̪ 1 (0 + 1) Southern Nuautl h s 2 (0 + 2) Suena s̪ 1 (0 + 1) Suyá ɣ s 2 (1 + 1) Taoripi f h s̪ 3 (0 + 3) Taushiro h x 2 (0 + 2) Tetun s̪ f h 3 (0 + 3) Tigak ɮ β s 3 (2 + 1) Tinputz β h s 3 (1 + 2) Tiwi ɣ 1 (1 + 0) Tongan; Tonga v f h s 4 (1 + 3) Trió h s 2 (0 + 2) Usan s 1 (0 + 1) Vanimo β ɦ s 3 (2 + 1) Waama f s 2 (0 + 2) Waiwai ʃ h s ɸ 4 (0 + 4) Wantoat s̪ 1 (0 + 1) Waorani 0 (0 + 0) Wari; Wari'; Wariʔ; Oro Nao h hʷ 2 (0 + 2) Warihio h s 2 (0 + 2) Waris β s̪ x 3 (1 + 2) Wik-Munkan 0 (0 + 0) Yabarana h s 2 (0 + 2) Yagaria v h s 3 (1 + 2) Yareba s ɸ 2 (0 + 2) Yawa sʲ s 2 (0 + 2) Yekwana h s 2 (0 + 2) Yidiny 0 (0 + 0) Yil s 1 (0 + 1)

## Nasals

In [15]:
langs_with_nasals = []
for inventory in inventories:
    nasals = []
    for segment in inventory['Segments']:
        try:
            if is_nasal(segment):
                nasals.append(segment)
        except KeyError:
            pass
    else:
        langs_with_nasals.append({inventory['LanguageName']: sorted(nasals)})

html_table = ['<font face="Doulos SIL" size=4em><table>']
html_table.append('<tr><td>Llengua</td><td>no. de nasals</td><td colspan=0>Nasals</td></tr>')
for lang in langs_with_nasals:
    for inv in sorted(lang):
        html_table.append('<tr>')
        html_table.append('<td>{}</td>'.format(inv))
        html_table.append('<td>{}</td>'.format(len(lang[inv])))
        for item in sorted(lang[inv]):
            html_table.append('<td>{}</td>'.format(item))
        html_table.append('</tr>')
else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))

Llengua no. de nasals Nasals Abau 2 m n Ache 4 m mb n̪d̪ ŋɡ Aguaruna 2 m n Ainu 2 m n Akawaio 2 m n̪ Akurio 2 m n Alabama 2 m n̪ Amahuaca 2 m n̪ Amanab 3 m n ŋ Angaatiha 4 m n ŋ ɲ Ao 3 m n ŋ Apalaí 2 m n Apinaye 4 mb nd ŋɡ ɲɟ Arabela 2 m n̪ Arára, Pará 3 m n ŋ Arikapú 2 m n Asmat 2 m n Au 2 m n Auca 4 m n ŋ ɲ Auyana 4 m mː n nː Awa Pit 3 m n ŋ Awtuw 3 m n ŋ Baining 6 m mb n nd ŋ ŋɡ Bandjalang 4 m n n̠ ŋ Barasano 0 Bariai 3 m n ŋ Barí 3 m n ɲ Baruga 2 m n Bésɨro 3 m n ɲ Biak 2 m n Biali 2 m n Biloxi 2 m n Binandere 2 m n Binumarien 2 m n Blackfoot 2 m n Bororo 2 m n̪ Cacua 3 m n ŋ Canela 4 m n ŋ ɲ Carijona 3 m n ɲ Cherokee 2 m n Chuave 2 m n Comanche 2 m n Crow 0 Cubeo 0 Dadibi 2 m n Dani 2 m n̪ Dera 3 m n̪ ŋ Dyirbal 4 m n ŋ ɲ Efik 4 m n ŋ ɲ Ekari 2 m n Endo 4 m n ŋ ɲ Faiwol 2 m n Fasu 2 m n Fuzhou 3 m n̪ ŋ Gadsup 2 m n̪ Gavião do Pará 2 m n Golin 2 m n Guajajara 4 m n ŋ ŋʷ Gugu-Yalandyi 4 m n̪ ŋ ɲ Hawaiian 2 m n̪ Huron 1 n Ikpeng 3 m n ŋ Imonda 2 m n Ingarikó 2 m n Irarutu 5 m mb n̪ n̪d̪ ŋɡ Isaka 0 Iwam 3 m n ŋ Jabutí 2 m n Jamamadí 2 m n Kaiabi 3 m n ŋ Karajá 0 Karitiana; Karitiâna 4 m n ŋ ɲ Katukína 3 m n ɲ Kaxuiâna 2 m n Kikamba 4 m n ŋ ɲ Kipsigis 4 m n ŋ ɲ Klao 0 Koiari 2 m n Kokama-Kokamilla 2 m n Krahô 3 m n ŋ Krinkati-Timbira 2 m n Kuikúro-Kalapálo 4 m n ŋ ɲ Kuot 3 m n ŋ Leti 2 m n Macushi 2 m n Malakmalak 4 m n n̠ ŋ Manam 3 m n ŋ Maori 3 m n ŋ Mapoyo 3 m n ɲ Maxakali 4 mb nd n̠d̠ʒ ŋɡ Mianmin 3 m n ŋ Mixe 2 m n Namia 2 m n Nandi 4 m n ŋ ɲ Nankina 3 m n ŋ Nasioi 2 m n̪ Nateni 0 Ngomba 0 Nimboran 3 m n̪ ŋ Ningil 3 m n ŋ North Marquesan 2 m n Northern Paiute 3 m n ŋ Nukak 0 Nɔmaa (NɔmaáNdɛ́) 4 m n ŋ ɲ Oneida 1 n Oro Win 2 m n Orokaiva 3 m n ŋ Palauan 2 m ŋ Panará 2 m n Pémono 3 m n ɲ Piraha 0 Pohnpeian 4 m mʷ n̪ ŋ Puinave 2 m n Rikbaktsa 2 m n Roro 2 m n̪ Rotokas 0 Sabane 2 m n Sabaot 4 m n ŋ ɲ Samo 1 m Sanuma; Sanumá 2 m n Sebei 4 m n̪ ŋ ɲ Seimat 3 m n ŋ Selaru 2 m n Seneca 2 m n̪ Sentani 2 m n̪ Shanenawa 2 m n Shawi 2 m n Shawnee 2 m n Shiriana 2 m n̪ Shuar 2 m n Skou 2 m n Southern Kiwai 2 m n̪ Southern Nuautl 2 m n Suena 2 m n̪ Suyá 4 m n ŋ ɲ Taoripi 1 m Taushiro 2 n ɲ Tetun 2 m n̪ Tigak 3 m n ŋ Tinputz 2 m n Tiwi 4 m n n̪ ŋ Tongan; Tonga 3 m n̪ ŋ Trió 2 m n Usan 5 m mb n nd ŋɡ Vanimo 3 m n n̠ Waama 2 m n Waiwai 3 m n ɲ Wantoat 8 m mb n̪ n̪d̪ ŋ ŋɡ ŋɡʷ ŋʷ Waorani 4 m n ŋ ɲ Wari; Wari'; Wariʔ; Oro Nao 4 m mˀ n nˀ Warihio 2 m n Waris 3 mb n̪d̪ ŋɡ Wik-Munkan 4 m n n̠ ŋ Yabarana 3 m n ɲ Yagaria 2 m n Yareba 2 m n Yawa 3 m n nʲ Yekwana 3 m n ɲ Yidiny 4 m n ŋ ɲ Yil 3 m n ŋ

## Líquides

Codi per comprovar els universals

 * Gairebé totes les llengües tenen almenys una líquida. 
 * Les lengües amb dues o més líquides generalment tenen una lateral i el
contrast lateral/no lateral. 


In [16]:
langs_with_liquides = []
at_least_one_liquid = 0
at_least_two_liquid = 0
has_laterality_contrast = 0
for inventory in inventories:
    liquides = []
    laterality = []
    for segment in inventory['Segments']:
        try:
            if is_liquid(segment):
                laterality.append(features_d[segment]['lateral'])
                liquides.append(segment)
        except KeyError:
            pass
        
    else:
        if len(liquides) >= 1:
            at_least_one_liquid += 1
        
        if len(liquides) >= 2:
            at_least_two_liquid += 1
            if laterality.count(True) > 0 and laterality.count(False) > 0:
                has_laterality_contrast += 1
            
        langs_with_liquides.append({inventory['LanguageName']: sorted(liquides)})

html_table = ['<font face="Doulos SIL" size=4em><table>']
html_table.append('<tr><td>Llengua</td><td>Numero de liquides</td><td colspan=0>Liquides</td></tr>')
for lang in langs_with_liquides:
    for inv in sorted(lang):
        html_table.append('<tr>')
        html_table.append('<td>{}</td>'.format(inv))
        html_table.append('<td>{}</td>'.format(len(lang[inv])))
        for item in sorted(lang[inv]):
            html_table.append('<td>{}</td>'.format(item))
        html_table.append('</tr>')
else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))

print("Tenen almenys, una líquida: {:2%} ({} / {})".format(at_least_one_liquid / len(inventories),
                                                         at_least_one_liquid,
                                                         len(inventories)))

print('{} {} {:.2%} ({} / {})'.format('Les lengües amb dues o més líquides generalment',
                                      'tenen una lateral i lateralitat contrastiva',
                                       has_laterality_contrast / at_least_two_liquid,
                                       has_laterality_contrast, at_least_two_liquid))

Llengua Numero de liquides Liquides Abau 1 ɾ Ache 1 ɺ̪ Aguaruna 1 ɾ Ainu 1 ɾ Akawaio 1 *R̪ Akurio 1 ɾ Alabama 1 l̪ Amahuaca 1 ɾ̪ Amanab 1 r Angaatiha 1 ɺ Ao 1 l Apalaí 1 ɾ Apinaye 1 ɽ Arabela 1 r̪ Arára, Pará 2 l ɾ Arikapú 1 ɾ Asmat 1 ɾ Au 1 ɾ Auca 0 Auyana 1 ɾ Awa Pit 1 l Awtuw 2 l ɾ Baining 2 l ɾ Bandjalang 2 l r Barasano 1 ɾ Bariai 2 l r Barí 1 r Baruga 1 ɾ Bésɨro 1 ɾ Biak 2 l r Biali 2 l ɾ Biloxi 0 Binandere 1 ɾ Binumarien 1 r Blackfoot 1 l Bororo 1 *R̪ Cacua 1 l Canela 1 ɾ Carijona 1 ɾ Cherokee 1 l Chuave 1 ɾ Comanche 0 Crow 0 Cubeo 1 ɺ̪ Dadibi 1 ɾ Dani 1 l̪ Dera 0 Dyirbal 3 l r ɻ Efik 0 Ekari 0 Endo 2 l r Faiwol 1 l Fasu 1 ɾ Fuzhou 1 l̪ Gadsup 0 Gavião do Pará 1 ɾ Golin 2 l r Guajajara 1 ɾ Gugu-Yalandyi 3 *R̪ l̪ ɻ Hawaiian 1 l̪ Huron 1 r Ikpeng 2 l ɾ Imonda 2 l r Ingarikó 1 ɾ Irarutu 1 ɾ̪ Isaka 0 Iwam 1 *R Jabutí 1 ɾ Jamamadí 1 ɾ Kaiabi 1 ɾ Karajá 2 l ɾ Karitiana; Karitiâna 1 ɾ Katukína 1 l Kaxuiâna 1 ɾ Kikamba 1 l Kipsigis 2 l r Klao 0 Koiari 1 ɾ Kokama-Kokamilla 1 ɾ Krahô 1 l Krinkati-Timbira 1 ɾ Kuikúro-Kalapálo 1 l Kuot 2 l r Leti 2 l r Macushi 1 ɾ Malakmalak 3 l l̠ r Manam 2 l ɾ Maori 1 ɾ Mapoyo 1 ɾ Maxakali 0 Mianmin 0 Mixe 0 Namia 2 l r Nandi 2 l ɾ Nankina 0 Nasioi 1 ɾ̪ Nateni 0 Ngomba 0 Nimboran 1 *R̪ Ningil 2 l r North Marquesan 1 r Northern Paiute 0 Nukak 1 ɾ Nɔmaa (NɔmaáNdɛ́) 1 l Oneida 1 l Oro Win 2 t̪ʙ ɾ Orokaiva 0 Palauan 2 l r Panará 1 ɾ Pémono 1 ɾ Piraha 0 Pohnpeian 2 l̪ r Puinave 0 Rikbaktsa 2 ɽ ɾ Roro 1 ɾ̪ Rotokas 1 ᴅ Sabane 1 l Sabaot 2 l r Samo 1 l Sanuma; Sanumá 1 l Sebei 3 l̪ r̪ ɾ̪ Seimat 1 l Selaru 2 l r Seneca 0 Sentani 0 Shanenawa 1 ɾ Shawi 1 ɾ Shawnee 1 l Shiriana 1 ɾ̪ Shuar 1 ɾ Skou 2 l r Southern Kiwai 1 *R̪ Southern Nuautl 2 l r Suena 1 ɾ̪ Suyá 1 ɾ Taoripi 1 l̪ Taushiro 1 ɾ Tetun 2 l̪ r̪ Tigak 1 r Tinputz 1 l Tiwi 3 l ɻ ɾ Tongan; Tonga 1 ɺ Trió 1 ɾ Usan 0 Vanimo 1 l Waama 0 Waiwai 2 ɺ ɾ Wantoat 0 Waorani 0 Wari; Wari'; Wariʔ; Oro Nao 1 ɾ Warihio 1 ɾ Waris 2 *R̪ l̪ Wik-Munkan 2 l r Yabarana 1 ɾ Yagaria 1 ʟ Yareba 1 ɾ Yawa 1 ɾ Yekwana 1 ɾ Yidiny 3 l r ɻ Yil 2 l r

Tenen almenys, una líquida: 83.750000% (134 / 160)
Les lengües amb dues o més líquides generalment tenen una lateral i lateralitat contrastiva 94.74% (36 / 38)


Comprovació dels universals de jerarquies
========================

## Totes les consonants

In [17]:
langs_hierarchy = []
for inventory in inventories:
    subsystems = []

    dentoalveolars = [segment for segment in inventory['Segments'] if features_d[segment]['coronal'] and not features_d[segment]['dorsal']]
    subsystems.append(dentoalveolars)

    labials = [segment for segment in inventory['Segments'] if features_d[segment]['labial']]
    subsystems.append(labials)

    velars = [segment for segment in inventory['Segments'] if features_d[segment]['dorsal'] and features_d[segment]['high'] and not features_d[segment]['continuant']]
    subsystems.append(velars)

    palatals = [segment for segment in inventory['Segments'] if features_d[segment]['coronal'] is True and features_d[segment]['dorsal'] is True]
    subsystems.append(palatals)
    
    langs_hierarchy.append({inventory['LanguageName']: subsystems})


html_table = ['<table>']

# Build header
html_table.append('<tr>')
for header in ['Llengua', 'Alveolars', 'Labials', 'Velars',
               'Palatals', 'Jerarquia (a &gt; l &gt; v  &gt; p)']:
    
    html_table.append('<td>{}</td>'.format(header))
    
else:
    html_table.append('<tr>')

# Add contents
for lang in langs_hierarchy:
    for inv in lang:
        if len(lang[inv][0]) == 0 and len(lang[inv][1]) == 0 and len(lang[inv][2]) == 0 and  len(lang[inv][3]) == 0:
            continue

        html_table.append('<tr>')
        html_table.append('<td>{}</td>'.format(inv))
        
        for item in lang[inv]:
            html_table.append('<td>{} [ {} ]</td>'.format(len(item), ' '.join(item)))
        
        follows_hierarchy = len(lang[inv][0]) >= len(lang[inv][1]) and len(lang[inv][1]) >= len(lang[inv][2])
        html_table.append('<td>{}<td>'.format("si" if follows_hierarchy else "no"))

    else:
        html_table.append('</tr>')
else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))

Llengua Alveolars Labials Velars Palatals Jerarquia (a > l > v > p) Abau 3 [ n s ɾ ] 3 [ m p w ] 1 [ k ] 0 [ ] si Ache 5 [ d̠ʒ t̠ʃ ɺ̪ n̪d̪ t̪ ] 4 [ β mb m p ] 2 [ ŋɡ k ] 0 [ ] si Aguaruna 7 [ ʃ ɾ ts s t n t̠ʃ ] 2 [ m p ] 1 [ k ] 0 [ ] si Ainu 5 [ n s t̠ʃ t ɾ ] 3 [ m p w ] 1 [ k ] 0 [ ] si Akawaio 6 [ d̪ *R̪ s̪ z̪ n̪ t̪ ] 4 [ b m p w ] 2 [ ɡ k ] 0 [ ] si Akurio 4 [ t̠ʃ n t ɾ ] 3 [ m p w ] 1 [ k ] 0 [ ] si Alabama 6 [ n̪ l̪ ɬ̪ s t̪ t̠ʃ ] 5 [ b m p w ɸ ] 1 [ k ] 0 [ ] si Amahuaca 6 [ s̪ t̠ʃ ɾ̪ θ n̪ t̪ ] 3 [ m p w ] 1 [ k ] 0 [ ] si Amanab 4 [ n s r t ] 5 [ b f m p w ] 3 [ ɡ k ŋ ] 0 [ ] no Angaatiha 4 [ n t̠ʃ t ɺ ] 3 [ m p w ] 3 [ ɲ ŋ k ] 1 [ ɲ ] si Ao 6 [ l s n t ɭ͓ z ] 3 [ w m p ] 3 [ cç k ŋ ] 1 [ cç ] si Apalaí 6 [ ʃ n s t z ɾ ] 3 [ m p w ] 1 [ k ] 0 [ ] si Apinaye 6 [ ʒ nd s̪ t̠ʃ t ɽ ] 3 [ mb p v ] 3 [ ɲɟ ŋɡ k ] 1 [ ɲɟ ] si Arabela 5 [ ʃ s̪ n̪ t̪ r̪ ] 3 [ m p w ] 1 [ k ] 0 [ ] si Arára, Pará 5 [ l n ɾ t̠ʃ t ] 3 [ m p w ] 2 [ ŋ k ] 0 [ ] si Arikapú 4 [ t̠ʃ n t ɾ ] 3 [ m p w ] 1 [ k ] 0 [ ] si Asmat 5 [ n s t̠ʃ t ɾ ] 4 [ f m p w ] 1 [ k ] 1 [ ʝ ] si Au 4 [ n s t ɾ ] 3 [ m p w ] 1 [ k ] 0 [ ] si Auca 3 [ d n t ] 4 [ b m p w ] 4 [ ŋ ɲ ɡ k ] 1 [ ɲ ] no Auyana 4 [ n t nː ɾ ] 4 [ m p w mː ] 1 [ k ] 0 [ ] si Awa Pit 8 [ ʃ ɬ ʒ l n s t̪ z ] 3 [ m p w ] 2 [ ŋ k ] 0 [ ] si Awtuw 5 [ d l tʰ n ɾ ] 3 [ pʰ m w ] 2 [ ŋ kʰ ] 0 [ ] si Baining 6 [ nd l n s t ɾ ] 4 [ mb m p w ] 3 [ ŋɡ ŋ k ] 0 [ ] si Bandjalang 6 [ d n̠ l n r d̠ʒ ] 3 [ b m w ] 2 [ ɡ ŋ ] 0 [ ] si Barasano 4 [ d s t ɾ ] 3 [ b p w ] 2 [ ɡ k ] 0 [ ] si Bariai 6 [ d l n s r t ] 3 [ b m p ] 3 [ ɡ k ŋ ] 0 [ ] si Barí 5 [ d n s r t ] 2 [ b m ] 2 [ ɲ k ] 1 [ ɲ ] si Baruga 6 [ d̠ʒ d n s t ɾ ] 4 [ β b m ɸ ] 2 [ ɡ k ] 0 [ ] si Bésɨro 7 [ ʃ ʂ t̠ʃ n s t ɾ ] 3 [ β m p ] 3 [ c k ɲ ] 2 [ c ɲ ] si Biak 6 [ d l n s r t ] 6 [ β b f m p w ] 1 [ k ] 0 [ ] si Biali 6 [ d l n s t ɾ ] 5 [ b f m p w ] 1 [ k ] 0 [ ] si Biloxi 4 [ d n s t ] 3 [ p m w ] 2 [ c k ] 1 [ c ] si Binandere 4 [ d n t ɾ ] 4 [ β b m p ] 2 [ ɡ k ] 0 [ ] si Binumarien 4 [ t s r n ] 4 [ m p w ɸ ] 1 [ k ] 0 [ ] si Blackfoot 5 [ t̪ t̠ʃ l n s ] 3 [ m p w ] 1 [ k ] 0 [ ] si Bororo 6 [ n̪ d̪ *R̪ t̪ d̠ʒ t̠ʃ ] 4 [ b m p w ] 2 [ ɡ k ] 0 [ ] si Cacua 4 [ l n t̠ʃ t ] 4 [ ʍ m p w ] 2 [ ŋ k ] 0 [ ] si Canela 4 [ t̠ʃ n t ɾ ] 3 [ m p w ] 3 [ ŋ k ɲ ] 1 [ ɲ ] si Carijona 7 [ d̠ʒ t̠ʃ d n s t ɾ ] 3 [ b m w ] 3 [ ɡ k ɲ ] 1 [ ɲ ] si Cherokee 5 [ ʃ d l n dz ] 2 [ m w ] 1 [ ɡ ] 0 [ ] si Chuave 5 [ d n s t ɾ ] 4 [ b f m w ] 2 [ ɡ k ] 0 [ ] si Comanche 4 [ n s t̪ t̪s̪ ] 4 [ m p w kʷ ] 2 [ k kʷ ] 0 [ ] si Crow 5 [ ʃ s̪ t̠ʃ t̪ ɹ ] 2 [ p w ] 1 [ k ] 0 [ ] si Cubeo 6 [ d̠ ɺ̪ d ð t̠ʃ t ] 3 [ p β b ] 1 [ k ] 0 [ ] si Dadibi 5 [ tʰ n s t ɾ ] 4 [ pʰ m p w ] 2 [ kʰ k ] 0 [ ] si Dani 4 [ s̪ n̪ l̪ t̪ ] 4 [ m kʷ p w ] 2 [ kʷ k ] 0 [ ] si Dera 3 [ n̪ d̪ t̪ ] 4 [ b m p w ] 3 [ ɡ k ŋ ] 0 [ ] no Dyirbal 5 [ l n r ɻ d ] 3 [ b m w ] 4 [ ɡ ŋ ɲ ɟ ] 2 [ ɲ ɟ ] no Efik 4 [ d n s t ] 5 [ b f m kp w ] 4 [ ɲ k kp ŋ ] 1 [ ɲ ] no Ekari 3 [ d n t ] 4 [ b m p w ] 2 [ ɡˡ k ] 0 [ ] no Endo 5 [ r l n s t ] 3 [ m p w ] 4 [ ŋ c k ɲ ] 2 [ c ɲ ] no Faiwol 5 [ d l n s t ] 4 [ b f m w ] 2 [ ɡ k ] 0 [ ] si Fasu 4 [ n s t ɾ ] 4 [ ɸ m p w ] 1 [ k ] 0 [ ] si Fuzhou 7 [ l̪ s̪ t̪ n̪ t̪ʰ t̪s̪ t̪s̪ʰ ] 3 [ pʰ m p ] 3 [ kʰ ŋ k ] 0 [ ] si Gadsup 3 [ n̪ d t ] 3 [ m p β ] 1 [ k ] 0 [ ] si Gavião do Pará 4 [ t̠ʃ n t ɾ ] 3 [ m p w ] 2 [ kʰ k ] 0 [ ] si Golin 6 [ d l n s r t ] 4 [ m b p w ] 2 [ ɡ k ] 0 [ ] si Guajajara 5 [ ts t̪ n z ɾ ] 5 [ ŋʷ kʷ m p w ] 4 [ ŋʷ kʷ ŋ k ] 0 [ ] si Gugu-Yalandyi 5 [ n̪ l̪ *R̪ t̪ ɻ ] 3 [ m p w ] 4 [ c k ɲ ŋ ] 2 [ c ɲ ] no Hawaiian 2 [ n̪ l̪ ] 3 [ m p w ] 1 [ k ] 0 [ ] no Huron 5 [ n s r θ t ] 1 [ w ] 1 [ k ] 0 [ ] si Ikpeng 5 [ l n t t̠ʃ ɾ ] 3 [ w m p ] 3 [ ɡ k ŋ ] 0 [ ] si Imonda 6 [ d l n s r t ] 4 [ b f m p ] 2 [ ɡ k ] 0 [ ] si Ingarikó 4 [ n s t ɾ ] 3 [ m p w ] 1 [ k ] 0 [ ] si Irarutu 5 [ n̪d̪ n̪ s̪ ɾ̪ t̪ ] 4 [ mb m w ɸ ] 2 [ k ŋɡ ] 1 [ ʝ ] si Isaka 3 [ d s t ] 4 [ b p w ɸ ] 1 [ k ] 0 [ ] no Iwam 4 [ *R n s t ] 3 [ m p w ] 2 [ ŋ k ] 0 [ ] si Jabutí 7 [ ps d̠ʒ t̠ʃ bz n t ɾ

## Oclusives

### Jerarquia de les oclusives

In [18]:
langs_plosive_hierarchy = []
for inventory in inventories:
    subsystems = []

    dentoalveolars = [segment for segment in inventory['Segments'] if is_plosive(segment) and features_d[segment]['coronal'] and not features_d[segment]['dorsal']]
    subsystems.append(dentoalveolars)

    labials = [segment for segment in inventory['Segments'] if is_plosive(segment) and features_d[segment]['labial']]
    subsystems.append(labials)

    velars = [segment for segment in inventory['Segments'] if is_plosive(segment) and features_d[segment]['dorsal'] and features_d[segment]['high'] and not features_d[segment]['continuant']]
    subsystems.append(velars)

    palatals = [segment for segment in inventory['Segments'] if is_plosive(segment) and features_d[segment]['coronal'] is True and features_d[segment]['dorsal'] is True]
    subsystems.append(palatals)
    
    langs_plosive_hierarchy.append({inventory['LanguageName']: subsystems})


html_table = ['<table>']

# Build header
html_table.append('<tr>')
for header in ['Llengua', 'Oclusives alveolars', 'Oclusives labials', 'Oclusives Velars',
               'Oclusives Palatals', 'Jerarquia oclusives (a &gt; l &gt; v  &gt; p)']:
    
    html_table.append('<td>{}</td>'.format(header))
    
else:
    html_table.append('<tr>')

# Add contents
followers = 0

for lang in langs_plosive_hierarchy:
    for inv in lang:
        if len(lang[inv][0]) == 0 and len(lang[inv][1]) == 0 and len(lang[inv][2]) == 0 and  len(lang[inv][3]) == 0:
            continue
        html_table.append('<tr>')
        html_table.append('<td>{}</td>'.format(inv))
        
        for item in lang[inv]:
            html_table.append('<td>{} [ {} ]</td>'.format(len(item), ' '.join(item)))
        
        follows_hierarchy = len(lang[inv][0]) >= len(lang[inv][1]) and len(lang[inv][1]) >= len(lang[inv][2])
        if follows_hierarchy:
            followers +=1 
            
        html_table.append('<td>{}<td>'.format("si" if follows_hierarchy else "no"))

    else:
        html_table.append('</tr>')
else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))
print('Followers: {:.2%} ({} / {})'.format(followers / len(inventories), followers, len(inventories)))

Llengua Oclusives alveolars Oclusives labials Oclusives Velars Oclusives Palatals Jerarquia oclusives (a > l > v > p) Abau 0 [ ] 1 [ p ] 1 [ k ] 0 [ ] no Ache 1 [ t̪ ] 1 [ p ] 1 [ k ] 0 [ ] si Aguaruna 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Ainu 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Akawaio 2 [ d̪ t̪ ] 2 [ b p ] 2 [ ɡ k ] 0 [ ] si Akurio 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Alabama 1 [ t̪ ] 2 [ b p ] 1 [ k ] 0 [ ] no Amahuaca 1 [ t̪ ] 1 [ p ] 1 [ k ] 0 [ ] si Amanab 1 [ t ] 2 [ b p ] 2 [ ɡ k ] 0 [ ] no Angaatiha 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Ao 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Apalaí 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Apinaye 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Arabela 1 [ t̪ ] 1 [ p ] 1 [ k ] 0 [ ] si Arára, Pará 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Arikapú 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Asmat 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Au 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Auca 2 [ d t ] 2 [ b p ] 2 [ ɡ k ] 0 [ ] si Auyana 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Awa Pit 1 [ t̪ ] 1 [ p ] 1 [ k ] 0 [ ] si Awtuw 2 [ d tʰ ] 1 [ pʰ ] 1 [ kʰ ] 0 [ ] si Baining 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Bandjalang 1 [ d ] 1 [ b ] 1 [ ɡ ] 0 [ ] si Barasano 2 [ d t ] 2 [ b p ] 2 [ ɡ k ] 0 [ ] si Bariai 2 [ d t ] 2 [ b p ] 2 [ ɡ k ] 0 [ ] si Barí 2 [ d t ] 1 [ b ] 1 [ k ] 0 [ ] si Baruga 2 [ d t ] 1 [ b ] 2 [ ɡ k ] 0 [ ] no Bésɨro 1 [ t ] 1 [ p ] 2 [ c k ] 1 [ c ] no Biak 2 [ d t ] 2 [ b p ] 1 [ k ] 0 [ ] si Biali 2 [ d t ] 2 [ b p ] 1 [ k ] 0 [ ] si Biloxi 2 [ d t ] 1 [ p ] 2 [ c k ] 1 [ c ] no Binandere 2 [ d t ] 2 [ b p ] 2 [ ɡ k ] 0 [ ] si Binumarien 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Blackfoot 1 [ t̪ ] 1 [ p ] 1 [ k ] 0 [ ] si Bororo 2 [ d̪ t̪ ] 2 [ b p ] 2 [ ɡ k ] 0 [ ] si Cacua 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Canela 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Carijona 2 [ d t ] 1 [ b ] 2 [ ɡ k ] 0 [ ] no Cherokee 1 [ d ] 0 [ ] 1 [ ɡ ] 0 [ ] no Chuave 2 [ d t ] 1 [ b ] 2 [ ɡ k ] 0 [ ] no Comanche 1 [ t̪ ] 2 [ p kʷ ] 2 [ k kʷ ] 0 [ ] no Crow 1 [ t̪ ] 1 [ p ] 1 [ k ] 0 [ ] si Cubeo 3 [ d̠ d t ] 2 [ p b ] 1 [ k ] 0 [ ] si Dadibi 2 [ tʰ t ] 2 [ pʰ p ] 2 [ kʰ k ] 0 [ ] si Dani 1 [ t̪ ] 2 [ kʷ p ] 2 [ kʷ k ] 0 [ ] no Dera 2 [ d̪ t̪ ] 2 [ b p ] 2 [ ɡ k ] 0 [ ] si Dyirbal 1 [ d ] 1 [ b ] 2 [ ɡ ɟ ] 1 [ ɟ ] no Efik 2 [ d t ] 2 [ b kp ] 2 [ k kp ] 0 [ ] si Ekari 2 [ d t ] 2 [ b p ] 2 [ ɡˡ k ] 0 [ ] si Endo 1 [ t ] 1 [ p ] 2 [ c k ] 1 [ c ] no Faiwol 2 [ d t ] 1 [ b ] 2 [ ɡ k ] 0 [ ] no Fasu 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Fuzhou 2 [ t̪ t̪ʰ ] 2 [ pʰ p ] 2 [ kʰ k ] 0 [ ] si Gadsup 2 [ d t ] 1 [ p ] 1 [ k ] 0 [ ] si Gavião do Pará 1 [ t ] 1 [ p ] 2 [ kʰ k ] 0 [ ] no Golin 2 [ d t ] 2 [ b p ] 2 [ ɡ k ] 0 [ ] si Guajajara 1 [ t̪ ] 2 [ kʷ p ] 2 [ kʷ k ] 0 [ ] no Gugu-Yalandyi 1 [ t̪ ] 1 [ p ] 2 [ c k ] 1 [ c ] no Hawaiian 0 [ ] 1 [ p ] 1 [ k ] 0 [ ] no Huron 1 [ t ] 0 [ ] 1 [ k ] 0 [ ] no Ikpeng 1 [ t ] 1 [ p ] 2 [ ɡ k ] 0 [ ] no Imonda 2 [ d t ] 2 [ b p ] 2 [ ɡ k ] 0 [ ] si Ingarikó 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Irarutu 1 [ t̪ ] 0 [ ] 1 [ k ] 0 [ ] no Isaka 2 [ d t ] 2 [ b p ] 1 [ k ] 0 [ ] si Iwam 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Jabutí 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Jamamadí 2 [ d t ] 1 [ b ] 2 [ k ɟ ] 1 [ ɟ ] no Kaiabi 1 [ t ] 2 [ kʷ p ] 3 [ kʷ ɡ k ] 0 [ ] no Karajá 2 [ ɗ d ] 1 [ b ] 1 [ k ] 0 [ ] si Karitiana; Karitiâna 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Katukína 2 [ d t ] 2 [ b p ] 1 [ k ] 0 [ ] si Kaxuiâna 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Kikamba 1 [ t ] 0 [ ] 1 [ k ] 0 [ ] no Kipsigis 1 [ tʰ ] 1 [ p ] 1 [ kʰ ] 0 [ ] si Klao 2 [ d̪ t̪ ] 4 [ ɡb b p kp ] 2 [ ɡb kp ] 0 [ ] no Koiari 2 [ d t ] 1 [ b ] 2 [ ɡ k ] 0 [ ] no Kokama-Kokamilla 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Krahô 1 [ t ] 1 [ p ] 2 [ kʰ k ] 0 [ ] no Krinkati-Timbira 1 [ t ] 1 [ p ] 2 [ kʰ k ] 0 [ ] no Kuikúro-Kalapálo 1 [ t ] 1 [ p ] 2 [ dʲ k ] 1 [ dʲ ] no Kuot 2 [ d t ] 2 [ b p ] 2 [ ɡ k ] 0 [ ] si Leti 2 [ d t ] 1 [ p ] 1 [ k ] 0 [ ] si Macushi 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Malakmalak 2 [ t t̠ ] 1 [ p ] 1 [ k ] 0 [ ] si Manam 2 [ d t ] 2 [ b p ] 2 [ ɡ k ] 0 [ ] si Maori 1 [ t ] 1 [ p ] 1 [ k ] 0 [ ] si Mapoyo 1 [ t

Followers: 63.75% (102 / 160)


### Jerarquia de les africades

In [19]:
langs_affricate_hierarchy = []
for inventory in inventories:
    subsystems = []
    
    palatals = [segment for segment in inventory['Segments'] if is_affricate(segment) and not features_d[segment]['anterior'] and features_d[segment]['coronal'] and not features_d[segment]['dorsal']]
    subsystems.append(palatals)

    dentoalveolars = [segment for segment in inventory['Segments'] if is_affricate(segment) and features_d[segment]['anterior'] and features_d[segment]['coronal'] and not features_d[segment]['dorsal']]
    subsystems.append(dentoalveolars)

    labials = [segment for segment in inventory['Segments'] if is_affricate(segment) and features_d[segment]['labial']]
    subsystems.append(labials)

    velars = [segment for segment in inventory['Segments'] if is_affricate(segment) and features_d[segment]['dorsal'] and features_d[segment]['high'] and not features_d[segment]['continuant']]
    subsystems.append(velars)
    
    langs_affricate_hierarchy.append({inventory['LanguageName']: subsystems})


html_table = ['<table>']

# Build header
html_table.append('<tr>')
for header in ['Llengua', 'Africades palatals', 'Africades dentoalveolars', 'Africades Velars',
               'Africades labials', 'Africades (p &gt; d &gt; v  &gt; l)']:
    
    html_table.append('<td>{}</td>'.format(header))
    
else:
    html_table.append('<tr>')

# Add contents
followers = 0
candidates = 0
for lang in langs_affricate_hierarchy:
    for inv in lang:
        if len(lang[inv][0]) == 0 and len(lang[inv][1]) == 0 and len(lang[inv][2]) == 0 and  len(lang[inv][3]) == 0:
            continue
        else:
            candidates += 1
            
        html_table.append('<tr>')
        html_table.append('<td>{}</td>'.format(inv))
        
        for item in lang[inv]:
            html_table.append('<td>{} [ {} ]</td>'.format(len(item), ' '.join(item)))
            
        follows_hierarchy = len(lang[inv][0]) >= len(lang[inv][1]) and len(lang[inv][1]) >= len(lang[inv][2])
        if follows_hierarchy:
            followers +=1
            
        html_table.append('<td>{}<td>'.format("si" if follows_hierarchy else "no"))

    else:
        html_table.append('</tr>')
else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))
print('Followers: {:.2%} ({} / {})'.format(followers / candidates, followers, candidates))

Llengua Africades palatals Africades dentoalveolars Africades Velars Africades labials Africades (p > d > v > l) Ache 2 [ d̠ʒ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Aguaruna 1 [ t̠ʃ ] 1 [ ts ] 0 [ ] 0 [ ] si Ainu 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Akurio 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Alabama 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Amahuaca 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Angaatiha 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Apinaye 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Arára, Pará 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Arikapú 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Asmat 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Bandjalang 1 [ d̠ʒ ] 0 [ ] 0 [ ] 0 [ ] si Baruga 1 [ d̠ʒ ] 0 [ ] 0 [ ] 0 [ ] si Bésɨro 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Blackfoot 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Bororo 2 [ d̠ʒ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Cacua 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Canela 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Carijona 2 [ d̠ʒ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Cherokee 0 [ ] 1 [ dz ] 0 [ ] 0 [ ] no Comanche 0 [ ] 1 [ t̪s̪ ] 0 [ ] 0 [ ] no Crow 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Cubeo 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Fuzhou 0 [ ] 2 [ t̪s̪ t̪s̪ʰ ] 0 [ ] 0 [ ] no Gavião do Pará 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Guajajara 0 [ ] 1 [ ts ] 0 [ ] 0 [ ] no Ikpeng 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Jabutí 2 [ d̠ʒ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Katukína 2 [ d̠ʒ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Kaxuiâna 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Kipsigis 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Kokama-Kokamilla 1 [ t̠ʃ ] 1 [ ts ] 0 [ ] 0 [ ] si Krahô 0 [ ] 1 [ ts ] 0 [ ] 0 [ ] no Krinkati-Timbira 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Kuikúro-Kalapálo 0 [ ] 1 [ ts ] 0 [ ] 0 [ ] no Maxakali 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Mixe 0 [ ] 1 [ ts͇ ] 0 [ ] 0 [ ] no Nankina 0 [ ] 2 [ ts dz ] 0 [ ] 0 [ ] no Ngomba 0 [ ] 1 [ dz ] 0 [ ] 0 [ ] no Northern Paiute 1 [ t̠ʃ ] 1 [ ts ] 0 [ ] 0 [ ] si Oneida 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Orokaiva 0 [ ] 1 [ dz ] 0 [ ] 0 [ ] no Pohnpeian 1 [ ʈʂ ] 0 [ ] 0 [ ] 0 [ ] si Rikbaktsa 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Sabaot 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Sanuma; Sanumá 0 [ ] 1 [ ts ] 0 [ ] 0 [ ] no Seneca 0 [ ] 1 [ d̪z̪ ] 0 [ ] 0 [ ] no Shanenawa 1 [ t̠ʃ ] 1 [ ts ] 0 [ ] 0 [ ] si Shawi 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Shawnee 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Shiriana 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Shuar 1 [ t̠ʃ ] 1 [ ts ] 0 [ ] 0 [ ] si Suena 0 [ ] 1 [ d̪z̪ ] 0 [ ] 0 [ ] no Suyá 2 [ d̠ʒ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Taushiro 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Waiwai 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Wari; Wari'; Wariʔ; Oro Nao 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Warihio 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si Yareba 0 [ ] 1 [ dz ] 0 [ ] 0 [ ] no Yawa 1 [ d̠ʒ ] 0 [ ] 0 [ ] 0 [ ] si Yekwana 1 [ t̠ʃ ] 0 [ ] 0 [ ] 0 [ ] si

Followers: 77.05% (47 / 61)


### Jerarquia de les fricatives

In [20]:
langs_fricative_hierarchy = []
for inventory in inventories:
    subsystems = []

    dentoalveolars = [segment for segment in inventory['Segments'] if is_fricative(segment) and features_d[segment]['coronal'] and not features_d[segment]['dorsal']]
    subsystems.append(dentoalveolars)

    labials = [segment for segment in inventory['Segments'] if is_fricative(segment) and features_d[segment]['labial']]
    subsystems.append(labials)
    
    palatals = [segment for segment in inventory['Segments'] if is_fricative(segment) and features_d[segment]['coronal'] is True and features_d[segment]['dorsal'] is True]
    subsystems.append(palatals)

    velars = [segment for segment in inventory['Segments'] if is_fricative(segment) and features_d[segment]['dorsal'] and features_d[segment]['high'] and not features_d[segment]['continuant']]
    subsystems.append(velars)
    
    langs_fricative_hierarchy.append({inventory['LanguageName']: subsystems})


html_table = ['<table>']

# Build header
html_table.append('<tr>')
for header in ['Llengua', 'fricatives alveolars', 'fricatives labials', 'fricatives palatals',
               'fricatives velars', 'Jerarquia fricatives (a &gt; l &gt; p  &gt; v)']:
    
    html_table.append('<td>{}</td>'.format(header))
    
else:
    html_table.append('<tr>')

# Add contents
followers = 0
for lang in langs_fricative_hierarchy:
    for inv in lang:
        if len(lang[inv][0]) == 0 and len(lang[inv][1]) == 0 and len(lang[inv][2]) == 0 and  len(lang[inv][3]) == 0:
            continue
        html_table.append('<tr>')
        html_table.append('<td>{}</td>'.format(inv))
        
        for item in lang[inv]:
            html_table.append('<td>{} [ {} ]</td>'.format(len(item), ' '.join(item)))
        
        follows_hierarchy = len(lang[inv][0]) >= len(lang[inv][1]) and len(lang[inv][1]) >= len(lang[inv][2])
        
        if follows_hierarchy:
            followers += 1
            
        html_table.append('<td>{}<td>'.format("si" if follows_hierarchy else "no"))

    else:
        html_table.append('</tr>')
else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))
print('Followers: {:.2%} ({} / {})'.format(followers / len(inventories), followers, len(inventories)))

Llengua fricatives alveolars fricatives labials fricatives palatals fricatives velars Jerarquia fricatives (a > l > p > v) Abau 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Ache 0 [ ] 1 [ β ] 0 [ ] 0 [ ] no Aguaruna 2 [ ʃ s ] 0 [ ] 0 [ ] 0 [ ] si Ainu 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Akawaio 2 [ s̪ z̪ ] 0 [ ] 0 [ ] 0 [ ] si Alabama 2 [ ɬ̪ s ] 1 [ ɸ ] 0 [ ] 0 [ ] si Amahuaca 2 [ s̪ θ ] 0 [ ] 0 [ ] 0 [ ] si Amanab 1 [ s ] 1 [ f ] 0 [ ] 0 [ ] si Ao 3 [ s ɭ͓ z ] 0 [ ] 0 [ ] 0 [ ] si Apalaí 3 [ ʃ s z ] 0 [ ] 0 [ ] 0 [ ] si Apinaye 2 [ ʒ s̪ ] 1 [ v ] 0 [ ] 0 [ ] si Arabela 2 [ ʃ s̪ ] 0 [ ] 0 [ ] 0 [ ] si Asmat 1 [ s ] 1 [ f ] 1 [ ʝ ] 0 [ ] si Au 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Awa Pit 5 [ ʃ ɬ ʒ s z ] 0 [ ] 0 [ ] 0 [ ] si Baining 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Barasano 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Bariai 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Barí 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Baruga 1 [ s ] 2 [ β ɸ ] 0 [ ] 0 [ ] no Bésɨro 3 [ ʃ ʂ s ] 1 [ β ] 0 [ ] 0 [ ] si Biak 1 [ s ] 2 [ β f ] 0 [ ] 0 [ ] no Biali 1 [ s ] 1 [ f ] 0 [ ] 0 [ ] si Biloxi 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Binandere 0 [ ] 1 [ β ] 0 [ ] 0 [ ] no Binumarien 1 [ s ] 1 [ ɸ ] 0 [ ] 0 [ ] si Blackfoot 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Cacua 0 [ ] 1 [ ʍ ] 0 [ ] 0 [ ] no Carijona 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Cherokee 1 [ ʃ ] 0 [ ] 0 [ ] 0 [ ] si Chuave 1 [ s ] 1 [ f ] 0 [ ] 0 [ ] si Comanche 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Crow 2 [ ʃ s̪ ] 0 [ ] 0 [ ] 0 [ ] si Cubeo 1 [ ð ] 1 [ β ] 0 [ ] 0 [ ] si Dadibi 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Dani 1 [ s̪ ] 0 [ ] 0 [ ] 0 [ ] si Efik 1 [ s ] 1 [ f ] 0 [ ] 0 [ ] si Endo 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Faiwol 1 [ s ] 1 [ f ] 0 [ ] 0 [ ] si Fasu 1 [ s ] 1 [ ɸ ] 0 [ ] 0 [ ] si Fuzhou 1 [ s̪ ] 0 [ ] 0 [ ] 0 [ ] si Gadsup 0 [ ] 1 [ β ] 0 [ ] 0 [ ] no Golin 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Guajajara 1 [ z ] 0 [ ] 0 [ ] 0 [ ] si Huron 2 [ s θ ] 0 [ ] 0 [ ] 0 [ ] si Imonda 1 [ s ] 1 [ f ] 0 [ ] 0 [ ] si Ingarikó 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Irarutu 1 [ s̪ ] 1 [ ɸ ] 1 [ ʝ ] 0 [ ] si Isaka 1 [ s ] 1 [ ɸ ] 0 [ ] 0 [ ] si Iwam 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Jabutí 2 [ ps bz ] 3 [ ps β bz ] 0 [ ] 0 [ ] no Jamamadí 1 [ s ] 1 [ ɸ ] 0 [ ] 0 [ ] si Kaiabi 1 [ s ] 1 [ ɸ ] 0 [ ] 0 [ ] si Karajá 1 [ θ ] 0 [ ] 0 [ ] 0 [ ] si Karitiana; Karitiâna 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Kaxuiâna 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Kikamba 2 [ ð s ] 1 [ β ] 0 [ ] 0 [ ] si Kipsigis 1 [ s ] 0 [ ] 1 [ ç ] 0 [ ] no Klao 1 [ s̪ ] 1 [ f ] 0 [ ] 0 [ ] si Koiari 1 [ ð ] 1 [ f ] 0 [ ] 0 [ ] si Kuikúro-Kalapálo 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Kuot 1 [ s ] 1 [ f ] 0 [ ] 0 [ ] si Leti 1 [ s ] 1 [ β ] 0 [ ] 0 [ ] si Macushi 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Manam 2 [ s z ] 0 [ ] 0 [ ] 0 [ ] si Maori 0 [ ] 1 [ f ] 0 [ ] 0 [ ] no Mapoyo 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Mianmin 1 [ s ] 1 [ f ] 0 [ ] 0 [ ] si Mixe 3 [ ʃ ʒ s̪ ] 1 [ v ] 0 [ ] 0 [ ] si Nandi 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Nankina 0 [ ] 1 [ β ] 0 [ ] 0 [ ] no Nateni 1 [ s ] 1 [ f ] 0 [ ] 0 [ ] si Nimboran 1 [ s̪ ] 0 [ ] 0 [ ] 0 [ ] si Ningil 1 [ s ] 1 [ ɸ ] 0 [ ] 0 [ ] si North Marquesan 1 [ s ] 2 [ f v ] 1 [ ç ] 0 [ ] no Northern Paiute 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Nɔmaa (NɔmaáNdɛ́) 1 [ s ] 1 [ f ] 0 [ ] 0 [ ] si Oneida 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Oro Win 1 [ s ] 1 [ β ] 0 [ ] 0 [ ] si Orokaiva 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Palauan 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Panará 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Pémono 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Piraha 1 [ s̪ ] 0 [ ] 0 [ ] 0 [ ] si Pohnpeian 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Puinave 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Rikbaktsa 1 [ ʃ ] 0 [ ] 0 [ ] 0 [ ] si Rotokas 0 [ ] 1 [ β ] 0 [ ] 0 [ ] no Sabane 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Sabaot 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Samo 1 [ s ] 1 [ f ] 0 [ ] 0 [ ] si Sanuma; Sanumá 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Sebei 1 [ s̪ ] 0 [ ] 0 [ ] 0 [ ] si Seimat 1 [ s ] 0 [ ] 0 [ ] 0 [ ] si Selaru 1 [ s ] 1 [ f ] 0 [ ] 0 [ ] si Seneca 1 [ s̪ ] 0 [ ] 0 [ ] 0 [ ] si Sentani 0 [ ] 1 [ f ] 0 [ ] 0 [ ] no Shanenawa 2 [ ʂ s ] 1 [ f ] 0 [ ] 0 [ ] si Shawi 2 [ ʃ s ] 1 [ β ] 0 [ ] 0 [ ] si Shawnee 2 [ ʃ θ ] 0 [ ] 0 [ ] 0 [ ] si Shiriana 2 [ ʃ s̪ ] 0 [ ] 0

Followers: 68.75% (110 / 160)


## Jerarquia de les nasals

In [21]:
# • Nasals:  Dento-alveolar > Labial > Velar > Palatal > Retroflexa.
langs_nasal_hierarchy = []
for inventory in inventories:
    subsystems = []

    dentoalveolars = [segment for segment in inventory['Segments'] if is_nasal(segment) and features_d[segment]['coronal'] and not features_d[segment]['dorsal']]
    subsystems.append(dentoalveolars)

    labials = [segment for segment in inventory['Segments'] if is_nasal(segment) and features_d[segment]['labial']]
    subsystems.append(labials)
    
    velars = [segment for segment in inventory['Segments'] if is_nasal(segment) and features_d[segment]['dorsal'] and features_d[segment]['high'] and not features_d[segment]['continuant'] and features_d[segment]['coronal'] is False ]
    subsystems.append(velars)
    
    palatals = [segment for segment in inventory['Segments'] if is_nasal(segment) and features_d[segment]['coronal'] is True and features_d[segment]['coronal'] is True and features_d[segment]['dorsal'] is True]
    subsystems.append(palatals)
    
    langs_nasal_hierarchy.append({inventory['LanguageName']: subsystems})


html_table = ['<table>']

# Build header
html_table.append('<tr>')
for header in ['Llengua', 'nasals alveolars', 'nasals labials', 'nasals velars',
               'nasals palatals', 'Jerarquia nasals (a &gt; l &gt; p  &gt; v)']:
    
    html_table.append('<td>{}</td>'.format(header))
    
else:
    html_table.append('<tr>')

candidates = 0
followers = 0
# Add contents
for lang in langs_nasal_hierarchy:
    candidates += 1
    
    for inv in lang:
        if len(lang[inv][0]) == 0 and len(lang[inv][1]) == 0 and len(lang[inv][2]) == 0 and  len(lang[inv][3]) == 0:
            continue
        html_table.append('<tr>')
        html_table.append('<td>{}</td>'.format(inv))
        
        for item in lang[inv]:
            html_table.append('<td>{} [ {} ]</td>'.format(len(item), ' '.join(item)))
        
        follows_hierarchy = len(lang[inv][0]) >= len(lang[inv][1]) and len(lang[inv][1]) >= len(lang[inv][2])
        html_table.append('<td>{}<td>'.format("si" if follows_hierarchy else "no"))
        

    else:
        if follows_hierarchy:
            followers += 1
        html_table.append('</tr>')
else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))
print('Followers: {:.2%} ({} / {})'.format(followers / candidates, followers, candidates))

Llengua nasals alveolars nasals labials nasals velars nasals palatals Jerarquia nasals (a > l > p > v) Abau 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Ache 1 [ n̪d̪ ] 2 [ mb m ] 1 [ ŋɡ ] 0 [ ] no Aguaruna 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Ainu 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Akawaio 1 [ n̪ ] 1 [ m ] 0 [ ] 0 [ ] si Akurio 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Alabama 1 [ n̪ ] 1 [ m ] 0 [ ] 0 [ ] si Amahuaca 1 [ n̪ ] 1 [ m ] 0 [ ] 0 [ ] si Amanab 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Angaatiha 1 [ n ] 1 [ m ] 1 [ ŋ ] 1 [ ɲ ] si Ao 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Apalaí 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Apinaye 1 [ nd ] 1 [ mb ] 1 [ ŋɡ ] 1 [ ɲɟ ] si Arabela 1 [ n̪ ] 1 [ m ] 0 [ ] 0 [ ] si Arára, Pará 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Arikapú 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Asmat 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Au 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Auca 1 [ n ] 1 [ m ] 1 [ ŋ ] 1 [ ɲ ] si Auyana 2 [ n nː ] 2 [ m mː ] 0 [ ] 0 [ ] si Awa Pit 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Awtuw 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Baining 2 [ nd n ] 2 [ mb m ] 2 [ ŋɡ ŋ ] 0 [ ] si Bandjalang 2 [ n̠ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Bariai 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Barí 1 [ n ] 1 [ m ] 0 [ ] 1 [ ɲ ] si Baruga 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Bésɨro 1 [ n ] 1 [ m ] 0 [ ] 1 [ ɲ ] si Biak 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Biali 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Biloxi 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Binandere 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Binumarien 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Blackfoot 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Bororo 1 [ n̪ ] 1 [ m ] 0 [ ] 0 [ ] si Cacua 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Canela 1 [ n ] 1 [ m ] 1 [ ŋ ] 1 [ ɲ ] si Carijona 1 [ n ] 1 [ m ] 0 [ ] 1 [ ɲ ] si Cherokee 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Chuave 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Comanche 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Dadibi 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Dani 1 [ n̪ ] 1 [ m ] 0 [ ] 0 [ ] si Dera 1 [ n̪ ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Dyirbal 1 [ n ] 1 [ m ] 1 [ ŋ ] 1 [ ɲ ] si Efik 1 [ n ] 1 [ m ] 1 [ ŋ ] 1 [ ɲ ] si Ekari 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Endo 1 [ n ] 1 [ m ] 1 [ ŋ ] 1 [ ɲ ] si Faiwol 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Fasu 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Fuzhou 1 [ n̪ ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Gadsup 1 [ n̪ ] 1 [ m ] 0 [ ] 0 [ ] si Gavião do Pará 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Golin 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Guajajara 1 [ n ] 2 [ ŋʷ m ] 2 [ ŋʷ ŋ ] 0 [ ] no Gugu-Yalandyi 1 [ n̪ ] 1 [ m ] 1 [ ŋ ] 1 [ ɲ ] si Hawaiian 1 [ n̪ ] 1 [ m ] 0 [ ] 0 [ ] si Huron 1 [ n ] 0 [ ] 0 [ ] 0 [ ] si Ikpeng 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Imonda 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Ingarikó 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Irarutu 2 [ n̪d̪ n̪ ] 2 [ mb m ] 1 [ ŋɡ ] 0 [ ] si Iwam 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Jabutí 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Jamamadí 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Kaiabi 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Karitiana; Karitiâna 1 [ n ] 1 [ m ] 1 [ ŋ ] 1 [ ɲ ] si Katukína 1 [ n ] 1 [ m ] 0 [ ] 1 [ ɲ ] si Kaxuiâna 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Kikamba 1 [ n ] 1 [ m ] 1 [ ŋ ] 1 [ ɲ ] si Kipsigis 1 [ n ] 1 [ m ] 1 [ ŋ ] 1 [ ɲ ] si Koiari 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Kokama-Kokamilla 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Krahô 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Krinkati-Timbira 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Kuikúro-Kalapálo 1 [ n ] 1 [ m ] 1 [ ŋ ] 1 [ ɲ ] si Kuot 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Leti 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Macushi 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Malakmalak 2 [ n̠ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Manam 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Maori 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Mapoyo 1 [ n ] 1 [ m ] 0 [ ] 1 [ ɲ ] si Maxakali 2 [ nd n̠d̠ʒ ] 1 [ mb ] 1 [ ŋɡ ] 0 [ ] si Mianmin 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Mixe 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Namia 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Nandi 1 [ n ] 1 [ m ] 1 [ ŋ ] 1 [ ɲ ] si Nankina 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Nasioi 1 [ n̪ ] 1 [ m ] 0 [ ] 0 [ ] si Nimboran 1 [ n̪ ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Ningil 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si North Marquesan 1 [ n ] 1 [ m ] 0 [ ] 0 [ ] si Northern Paiute 1 [ n ] 1 [ m ] 1 [ ŋ ] 0 [ ] si Nɔmaa (NɔmaáNdɛ́) 1 [ n ] 

Followers: 95.62% (153 / 160)


# Comprovació de més universals

### Presència o absència de /p t k/

In [22]:
ptk_in_language = 0
langs_with_ptk = []
langs_without_ptk = []
for inventory in inventories:
    inventory_segments = inventory['Segments']
    if 'p' in inventory_segments and 't' in inventory_segments and 'k' in inventory_segments:
        ptk_in_language += 1
        langs_with_ptk.append(inventory['LanguageName'])
    else:
        langs_without_ptk.append(inventory['LanguageName'])

print('Llengües amb /p t k/: {:.2%} ({} de {})'.format(ptk_in_language / len(inventories),
                                                       ptk_in_language,
                                                       len(inventories)))

Llengües amb /p t k/: 58.13% (93 de 160)


In [23]:
africades = []
for inventory in inventories:
    for segment in inventory['Segments']:
        try:
            if features_d[segment]['continuant'] is False \
            and features_d[segment]['sonorant'] is False \
            and features_d[segment]['continuant'] is False \
            and (features_d[segment]['strident'] is True or features_d[segment]['strident']):
            
                africades.append(segment)
        except KeyError:
            pass

africades = collections.Counter(africades)

html_table = ['<font face="Doulos SIL" size=4em><table>']
html_table.append('<tr><td>Fonema</td><td>Ocurrències</td>')
for k, v in africades.items():
    for inv in lang:
        html_table.append('<tr>')
        html_table.append('<td>{}</td><td>{}</td>'.format(k, v))

else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))

Fonema Ocurrències ts 10 t̠ʃ 43 d̠ʒ 9 dz 5 t̪s̪ 2 ʈʂ 1 d̪z̪ 2 ts͇ 1 t̪s̪ʰ 1

## Comprovació de l'universal "Si només té una africada, generalment és /t̠ʃ/"

In [24]:
followers = 0
possible_followers = 0
for inventory in inventories:
    affricates = [s for s in inventory['Segments'] if is_affricate(s)]
    if len(affricates) == 1:
        possible_followers += 1
        if affricates[0] == 't̠ʃ':
            followers += 1

else:
    print('Segueixen l\'universal {:.2%} ({} de {})'.format(followers / possible_followers,
                                                            followers,
                                                            possible_followers))

Segueixen l'universal 66.67% (32 de 48)


## Comprovació de l'universal "El nombre d’africades és menor que el d’oclusives simples."

In [25]:
followers = 0
possible_followers = 0
for inventory in inventories:
    affricates = [s for s in inventory['Segments'] if is_affricate(s)]
    plosives = [s for s in inventory['Segments'] if is_plosive(s)]
    possible_followers += 1
    
    if len(affricates) < len(plosives):
        followers += 1

else:
    print('Segueixen l\'universal {:.2%} ({} de {})'.format(followers / possible_followers,
                                                            followers,
                                                            possible_followers))

Segueixen l'universal 100.00% (160 de 160)


## Comprovació de l'universal "Si una llengua té una sola fricativa, generalment és / s / i si no és aquesta sol ser /f/."

In [26]:
followers_1st_part = 0
followers_2nd_part = 0
candidates = 0

for inventory in inventories:
    fricatives = [s for s in inventory['Segments'] if is_fricative(s)]
    
    if len(fricatives) == 1:
        candidates += 1
        if fricatives[0] == 's':
            followers_1st_part += 1
        elif fricatives[0] == 'f':
            followers_2nd_part += 1

else:
    print('Segueixen l\'universal primera part {:.2%} ({} de {})'.format(followers_1st_part / candidates,
                                                            followers_1st_part,
                                                            candidates))
    print('Segueixen l\'universal primera part {:.2%} ({} de {})'.format(followers_2nd_part / candidates,
                                                        followers_2nd_part,
                                                        candidates))
    print('Segueixen l\'universal (total) {:.2%} ({} de {})'.format((followers_1st_part + followers_2nd_part) / candidates,
                                                        (followers_1st_part + followers_2nd_part),
                                                        candidates))

Segueixen l'universal primera part 34.38% (11 de 32)
Segueixen l'universal primera part 0.00% (0 de 32)
Segueixen l'universal (total) 34.38% (11 de 32)


## Comprovació de l'universal "El nombre de fricatives sordes generalment és més gran que el de sonores…"

In [27]:
followers = 0
non_followers = []
candidates = len(langs_with_fricatives)
for lang in langs_with_fricatives:
    for _, v in lang.items():
        if len(v[0]) > 0 or len(v[1]) > 0:
            if len(v[1]) > len(v[0]):
                followers += 1
            else:
                non_followers.append(lang)

else:
    print('Segueixen l\'universal {:.2%} ({} de {})'.format(followers / candidates,
                                                        followers,
                                                        candidates))
    print("No el segueixen:",  non_followers)

Segueixen l'universal 73.12% (117 de 160)
No el segueixen: [{'Ache': [['β'], []]}, {'Akawaio': [['z̪'], ['s̪']]}, {'Ao': [['ɭ͓', 'z'], ['s']]}, {'Apinaye': [['ʒ', 'v'], ['s̪']]}, {'Au': [['ɣ'], ['s']]}, {'Baining': [['ɣ'], ['s']]}, {'Baruga': [['β', 'ɣ'], ['s', 'ɸ']]}, {'Binandere': [['β'], []]}, {'Cubeo': [['β', 'ð'], ['x']]}, {'Gadsup': [['β'], []]}, {'Guajajara': [['z'], ['h']]}, {'Jabutí': [['β', 'bz'], ['ps', 'h']]}, {'Kikamba': [['β', 'ð'], ['s']]}, {'Leti': [['β'], ['s']]}, {'Manam': [['z'], ['s']]}, {'Mixe': [['ʒ', 'v'], ['ʃ', 's̪']]}, {'Nankina': [['β'], []]}, {'Oro Win': [['β'], ['s']]}, {'Rotokas': [['β'], []]}, {'Suyá': [['ɣ'], ['s']]}, {'Tigak': [['ɮ', 'β'], ['s']]}, {'Tiwi': [['ɣ'], []]}, {'Vanimo': [['β', 'ɦ'], ['s']]}]


## Comprovació de l'universal "El nombre de fricatives improbablement és major que el d’oclusives."

In [28]:
candidates = 0
followers = []
for inventory in inventories:
    fricatives = [s for s in inventory['Segments'] if is_fricative(s)]
    plosives = [s for s in inventory['Segments'] if is_plosive(s)]
    
    if len(fricatives) > 0 or len(plosives) > 0:
        candidates += 1
        if len(fricatives) > len(plosives):
            followers.append(inventory['LanguageName'])
else:
    print('Segueixen l\'universal {:.2%} ({} de {})'.format(len(followers) / candidates,
                                                        len(followers),
                                                        candidates))
    print('Llengües amb més fricatives que oclusives: {}'.format(', '.join(followers)))

Segueixen l'universal 5.62% (9 de 160)
Llengües amb més fricatives que oclusives: Awa Pit, Crow, Huron, Irarutu, Jabutí, Kikamba, North Marquesan, Shanenawa, Waiwai


## Comprovació dels universals sobre nasals

1. Preferència per l’articulació dento-alveolar.
2. Preferència per la sonoritat. 
3. Gairebé totes les llengües tenen almenys una nasal, generalment / n / Si hi ha una segona nasal generalment és /m / però també pot ser / ŋ / 
4. La presència de les nasals complexes implica la de les simples i la presència de nasals sordes implica la de les sonores. 

### Comprovació de 1

In [29]:
candidates = 0
followers = []
at_least_one_dentoalveolar = 0
not_at_least_one_dentoalveolar = []

for inventory in inventories:
    nasals = [s for s in inventory['Segments'] if is_nasal(s)]
    if len(nasals) == 0:
        continue
    
    candidates += 1
    dentoalveolar = [s for s in nasals if features_d[s]['coronal'] and not features_d[s]['dorsal']]
    not_dentoalveolar = [s for s in nasals if not (features_d[s]['coronal'] and not features_d[s]['dorsal'])]

    """
    print(inventory['LanguageName'])
    print("\tnasals:", nasals)
    print("\tdento:", dentoalveolar)
    print("\tno dento:", not_dentoalveolar)
    """
    
    if len(dentoalveolar) > 0:
        at_least_one_dentoalveolar += 1
    else:
        not_at_least_one_dentoalveolar.append(inventory)
    
    if len(dentoalveolar) >= len(not_dentoalveolar):
        followers.append(inventory['LanguageName'])


print('Tenen, almenys, una nasal dentoalveolar: {:.2%} ({} de {})'.format(at_least_one_dentoalveolar / candidates,
                                                       at_least_one_dentoalveolar,
                                                       candidates))

print('Tenen tantes o més dentoalveolars que no dentoalveolars {:.2%} ({} de {})'.format(len(followers) / candidates,
                                                                                         len(followers),
                                                                                        candidates))    

Tenen, almenys, una nasal dentoalveolar: 97.99% (146 de 149)
Tenen tantes o més dentoalveolars que no dentoalveolars 55.70% (83 de 149)


### Comprovació de 2

In [30]:
candidates = 0
followers = []
not_followers = []

for inventory in inventories:
    nasals = [s for s in inventory['Segments'] if is_nasal(s)]
    if len(nasals) == 0:
        continue
    
    candidates += 1
    voiced = [s for s in nasals if features_d[s]['periodicGlottalSource']]
    voiceless = [s for s in nasals if not features_d[s]['periodicGlottalSource']]

    if len(voiced) > len(voiceless):
        followers.append(inventory['LanguageName'])
    else:
        not_followers.append(inventory['LanguageName'])


print('Tenen més nasals sonores que sordes: {:.2%} ({} de {})'.format(len(followers) / candidates, len(followers), candidates))

Tenen més nasals sonores que sordes: 100.00% (149 de 149)


In [31]:
candidates = 0
followers_1 = []
followers_2 = []
followers_3 = []
non_followers = []

for inventory in inventories:
    nasals = [s for s in inventory['Segments'] if is_nasal(s)]
    if len(nasals) == 0:
        continue
    
    candidates += 1
    
    if len(nasals) >= 1 and 'n' in nasals:
        followers_1.append(inventory)
    else:
        non_followers.append(inventory)

    if len(nasals) >= 2 and 'n' in nasals and 'ŋ' in nasals:
        followers_2.append(inventory)
        
    elif len(nasals) >= 2 and 'n' in nasals and 'm' in nasals:
        followers_3.append(inventory)
        
    else:
        non_followers.append(inventory)
    
print('Tenen almenys una nasal, /n/. {:.2%} ({} de {})'.format(len(followers_1) / candidates, len(followers_1), candidates))
print('Tenen almenys dues nasals: n i ŋ. {:.2%} ({} de {})'.format(len(followers_2) / candidates, len(followers_2), candidates))
print('Tenen almenys dues nasals: n i m. {:.2%} ({} de {})'.format(len(followers_3) / candidates, len(followers_3), candidates))

Tenen almenys una nasal, /n/. 78.52% (117 de 149)
Tenen almenys dues nasals: n i ŋ. 29.53% (44 de 149)
Tenen almenys dues nasals: n i m. 46.98% (70 de 149)


# Ultra-mega-taula

![ZOMG](http://i.imgur.com/RJ6S6eY.gif)

In [32]:
html_table = ['<font face="Doulos SIL" size=4em><table>']
html_table.append('<tr><td>')

for consonant in all_consonants_uniq:
    html_table.append('<td>{}</td>'.format(consonant))

for inventory in inventories:
    html_table.append('<tr>')
    html_table.append('<td>{}</td>'.format(inventory['LanguageName']))

    count = 0
    for consonant in all_consonants_uniq:
        if consonant in inventory['Segments']:
            html_table.append('<td>X</td>')
            count += 1
        else:
            html_table.append('<td> </td>')
    else:
        html_table.append('<td>{}</td>'.format(count))
        html_table.append('</tr>')
        assert count == len(inventory['Segments'])

html_table.append('</table></font>')  
display(HTML(''.join(html_table)))

k m p w n t j s h b ɾ ʔ ŋ l d t̠ʃ ɡ t̪ r ɲ n̪ f s̪ β ʃ d̪ x ɸ c l̪ ts d̠ʒ kʷ mb ŋɡ kʰ ɾ̪ *R̪ ɟ ɣ dz v z kp nd n̠ n̪d̪ tʰ ɻ θ pʰ r̪ ð ɺ ʒ cç d̠ d̪z̪ t̠ t̪s̪ t̪ʰ ç ŋʷ ɗ ɹ ɺ̪ ɽ ʂ ʝ *R bv bz dʲ hʷ kː l̠ mʷ mˀ mː nʲ nˀ nː n̠d̠ʒ n̪z̪ ps pʷ sʲ ts͇ t̪s̪ʰ t̪ʙ t̺ z̪ ŋɡʷ ɓ ɟʝ ɡb ɡˡ ɥ ɦ ɬ ɬ̪ ɭ͓ ɮ ɰ ɲɟ ʈʂ ʍ ʟ ᴅ Abau X X X X X X X X X 9 Ache X X X X X X X X X X X 11 Aguaruna X X X X X X X X X X X X 12 Ainu X X X X X X X X X X X 11 Akawaio X X X X X X X X X X X X X 13 Akurio X X X X X X X X X X 10 Alabama X X X X X X X X X X X X X X 14 Amahuaca X X X X X X X X X X X X X X 14 Amanab X X X X X X X X X X X X X X 14 Angaatiha X X X X X X X X X X X X 12 Ao X X X X X X X X X X X X X X 14 Apalaí X X X X X X X X X X X X 12 Apinaye X X X X X X X X X X X X X 13 Arabela X X X X X X X X X X X 11 Arára, Pará X X X X X X X X X X X 11 Arikapú X X X X X X X X X X X 11 Asmat X X X X X X X X X X X 11 Au X X X X X X X X X X 10 Auca X X X X X X X X X X X 11 Auyana X X X X X X X X X X X 11 Awa Pit X X X X X X X X X X X X X X 14 Awtuw X X X X X X X X X X X 11 Baining X X X X X X X X X X X X X X 14 Bandjalang X X X X X X X X X X X X 12 Barasano X X X X X X X X X X X 11 Bariai X X X X X X X X X X X X 12 Barí X X X X X X X X X X 10 Baruga X X X X X X X X X X X X X X 14 Bésɨro X X X X X X X X X X X X X X 14 Biak X X X X X X X X X X X X X X 14 Biali X X X X X X X X X X X X X X 14 Biloxi X X X X X X X X X X X X 12 Binandere X X X X X X X X X X X 11 Binumarien X X X X X X X X X X X 11 Blackfoot X X X X X X X X X X X X X 13 Bororo X X X X X X X X X X X X X 13 Cacua X X X X X X X X X X X X 12 Canela X X X X X X X X X X X X X 13 Carijona X X X X X X X X X X X X X X 14 Cherokee X X X X X X X X X X X 11 Chuave X X X X X X X X X X X X 12 Comanche X X X X X X X X X X X X 12 Crow X X X X X X X X X X 10 Cubeo X X X X X X X X X X X 11 Dadibi X X X X X X X X X X X X X 13 Dani X X X X X X X X X X X X 12 Dera X X X X X X X X X X X 11 Dyirbal X X X X X X X X X X X X X 13 Efik X X X X X X X X X X X X X 13 Ekari X X X X X X X X X X 10 Endo X X X X X X X X X X X X X 13 Faiwol X X X X X X X X X X X X 12 Fasu X X X X X X X X X X X 11 Fuzhou X X X X X X X X X X X X X X 14 Gadsup X X X X X X X X X 9 Gavião do Pará X X X X X X X X X X X 11 Golin X X X X X X X X X X X X X 13 Guajajara X X X X X X X X X X X X X X 14 Gugu-Yalandyi X X X X X X X X X X X X X 13 Hawaiian X X X X X X X X 8 Huron X X X X X X X X X X X 11 Ikpeng X X X X X X X X X X X X 12 Imonda X X X X X X X X X X X X X 13 Ingarikó X X X X X X X X X X 10 Irarutu X X X X X X X X X X X X 12 Isaka X X X X X X X X X 9 Iwam X X X X X X X X X X X 11 Jabutí X X X X X X X X X X X X X X 14 Jamamadí X X X X X X X X X X X X 12 Kaiabi X X X X X X X X X X X X X X 14 Karajá X X X X X X X X X 9 Karitiana; Karitiâna X X X X X X X X X X X 11 Katukína X X X X X X X X X X X X 12 Kaxuiâna X X X X X X X X X X X X 12 Kikamba X X X X X X X X X X X X X 13 Kipsigis X X X X X X X X X X X X X X 14 Klao X X X X X X X X X X X 11 Koiari X X X X X X X X X X X 11 Kokama-Kokamilla X X X X X X X X X X X 11 Krahô X X X X X X X X X X X X 12 Krinkati-Timbira X X X X X X X X X X X 11 Kuikúro-Kalapálo X X X X X X X X X X X X X X 14 Kuot X X X X X X X X X X X X X 13 Leti X X X X X X X X X X 10 Macushi X X X X X X X X X X 10 Malakmalak X X X X X X X X X X X X X X 14 Manam X X X X X X X X X X X X X 13 Maori X X X X X X X X X X 10 Mapoyo X X X X X X X X X X X X 12 Maxakali X X X X X X X X X X 10 Mianmin X X X X X X X X X X X X X 13 Mixe X X X X X X X X X X X X X X 14 Namia X X X X X X X X X 9 Nandi X X X X X X X X X X X X X 13 Nankina X X X X X X X X X X X X X X 14 Nasioi X X X X X X X X 8 Nateni X X X X X X X X X X X X X 13 Ngomba X X X X X X X X X 9 Nimboran X X X X X X X X X X X X 12 Ningil X X X X X X X X X X X X X X 14 North Marquesan X X X X X X X X X X X X 12 Northern Paiute X X X X X X X X X X X X X X 14 Nukak X X X X X X X X X X X X 12 Nɔmaa (NɔmaáNdɛ́) X X X X X X X X X X X X X X 14 Oneida X X X X X X X X X X 10 Oro Win X X X X X X X X X X X X 12

In [33]:
family_tree = []
for inventory in inventories:
    family = inventory['LanguageFamilyRoot']
    genus = inventory['LanguageFamilyGenus']
    name = inventory['LanguageName']
    
    print('{}\t{}\t{}'.format(family, genus, name))

Sepik	Upper Sepik	Abau
Tupian	Tupi-Guaraní	Ache
Jivaroan	Jivaroan	Aguaruna
Ainu	Ainu	Ainu
Cariban	Cariban	Akawaio
Cariban	Cariban	Akurio
Muskogean	Muskogean	Alabama
Panoan	Panoan	Amahuaca
Border	Border	Amanab
Trans-New Guinea	Angan	Angaatiha
Sino-Tibetan	Kuki-Chin	Ao
Cariban	Cariban	Apalaí
Macro-Ge	Ge-Kaingang	Apinaye
Zaparoan	Zaparoan	Arabela
Cariban	Cariban	Arára, Pará
Jabutí	Jabutí	Arikapú
Trans-New Guinea	Asmat-Kamoro	Asmat
Torricelli	Wapei-Palei	Au
Waorani	Waorani	Auca
Trans-New Guinea	Eastern Highlands	Auyana
Barbacoan	Barbacoan	Awa Pit
Sepik	Ram	Awtuw
Baining-Taulil	Baining	Baining
Australian	Pama-Nyungan	Bandjalang
Tucanoan	Tucanoan	Barasano
Austronesian	Oceanic	Bariai
Chibchan	Motilon	Barí
Trans-New Guinea	Binanderean	Baruga
Chiquito	Chiquito	Bésɨro
Austronesian	South Halmahera - West New Guinea	Biak
Niger-Congo	Gur	Biali
Siouan	Siouan	Biloxi
Trans-New Guinea	Binanderean	Binandere
Trans-New Guinea	Eastern Highlands	Binumarien
Algic	Algonquian	Blackfoot
Macro-Ge	Bororo	Bo

In [34]:
print('{"type": "FeatureCollection", "features": [')

for inventory in inventories:
    lon, lat = inventory['Longitude'], inventory['Latitude']
    if lon == 'NULL':
        continue
    else:
        lon = lon.replace(':', '.')
        lat = lat.replace(':', '.')

        print('\t{"type": "Feature", "geometry": {"type": "Point",', end='')
        print('"coordinates": ', end='')
        coords = '[{:.3f}, {:.3f}]'.format(float(lon), float(lat))
        print(coords, end='')
        print('}, "properties": {}},')

print('], "properties": {}}')

{"type": "FeatureCollection", "features": [
	{"type": "Feature", "geometry": {"type": "Point","coordinates": [141.100, -4.000]}, "properties": {}},
	{"type": "Feature", "geometry": {"type": "Point","coordinates": [-55.150, -25.200]}, "properties": {}},
	{"type": "Feature", "geometry": {"type": "Point","coordinates": [-78.000, -5.000]}, "properties": {}},
	{"type": "Feature", "geometry": {"type": "Point","coordinates": [143.000, 43.000]}, "properties": {}},
	{"type": "Feature", "geometry": {"type": "Point","coordinates": [-61.250, 6.300]}, "properties": {}},
	{"type": "Feature", "geometry": {"type": "Point","coordinates": [-55.400, 3.120]}, "properties": {}},
	{"type": "Feature", "geometry": {"type": "Point","coordinates": [-94.350, 30.450]}, "properties": {}},
	{"type": "Feature", "geometry": {"type": "Point","coordinates": [-73.000, -10.300]}, "properties": {}},
	{"type": "Feature", "geometry": {"type": "Point","coordinates": [141.100, -3.300]}, "properties": {}},
	{"type": "Feature",

In [35]:
def get_upsid(aggregated, consonants):
    with open(aggregated) as f:
        aggregated_data = [i for i in csv.DictReader(f, delimiter='\t')]

    with open(consonants) as f:
        segments = [segment for segment in csv.DictReader(f, delimiter='\t')]

    inventories = []
    for inventory in aggregated_data:
            inventory['Segments'] = []
            
            if inventory['Source'] == 'UPSID':
                for segment in segments:
                    if inventory['InventoryID'] == segment['InventoryID']:
                        inventory['Segments'].append(segment['Phoneme'])

                for key in ['Phonemes', 'Tones', 'Population', 'Trump', 'Country', 'Vowels']:
                    del inventory[key]

                inventories.append(inventory)

    else:
        return inventories

upsid_inv = get_upsid('phoible-aggregated.tsv', 'phoible-consonants.tsv')


In [36]:
candidates = 0
followers = 0
for inv in upsid_inv:
    candidates += 1
    
    try:
        voiced_fric = [i for i in inv['Segments'] if is_fricative(i) and features_d[i]['periodicGlottalSource']]
        voiceless_fric = [i for i in inv['Segments'] if is_fricative(i) and features_d[i]['periodicGlottalSource'] is False]
    except KeyError:
        pass
    
    if len(voiced_fric) < len(voiceless_fric):
        followers += 1
    

print('UPSID: el nombre de fricatives sonores és menor que el de sordes: segueixen l\'universal {:.2%} ({} de {})'.format(followers / candidates, followers, candidates))

candidates = 0
followers = 0
for inv in upsid_inv:
    candidates += 1
    
    try:
        fric = [i for i in inv['Segments'] if is_fricative(i)]
        affric = [i for i in inv['Segments'] if is_affricate(i)]
        plosiv = [i for i in inv['Segments'] if is_plosive(i)]

    except KeyError:
        pass
    
    if len(fric) < (len(plosiv) + len(affric)):
        followers += 1

print('UPSID: el nombre de fricatives improbablement es major que oclusives i africades junts: segueixen l\'universal {:.2%} ({} de {})'.format(followers / candidates, followers, candidates))

candidates = 0
followers = 0
for inv in upsid_inv:
    candidates += 1
    
    try:
        liquid = [i for i in inv['Segments'] if is_fricative(i)]

    except KeyError:
        pass
    
    if len(liquid) > 0:
        followers += 1

print('UPSID: Gairebé totes les llengües tenen almenys una líquida: segueixen l\'universal {:.2%} ({} de {})'.format(followers / candidates, followers, candidates))

candidates = 0
followers = 0
non_followers = []
for inv in upsid_inv:    
    try:
        laterals = [i for i in inv['Segments'] if features_d[i]['lateral']]
    except KeyError:
        pass
    
    if len(laterals) > 0:
        candidates += 1
        
        for lateral in laterals:
            f = features_d[lateral]
            if f['periodicGlottalSource'] and f['approximant']:
                followers += 1
                break
        else:
            if inv['LanguageName'] not in non_followers:
                non_followers.append(inv['LanguageName'])

print('UPSID: Una llengua amb una o més laterals té una aproximant lateral sonora.: segueixen l\'universal {:.2%} ({} de {})'.format(followers / candidates, followers, candidates))
print('       no el segueixen', ', '.join(non_followers))

UPSID: el nombre de fricatives sonores és menor que el de sordes: segueixen l'universal 76.05% (343 de 451)
UPSID: el nombre de fricatives improbablement es major que oclusives i africades junts: segueixen l'universal 91.57% (413 de 451)
UPSID: Gairebé totes les llengües tenen almenys una líquida: segueixen l'universal 93.13% (420 de 451)
UPSID: Una llengua amb una o més laterals té una aproximant lateral sonora.: segueixen l'universal 97.10% (368 de 379)
       no el segueixen AHTNA, CHUKCHI, EKARI, KABARDIAN, !XU, LUSHOOTSEED, TSESHAHT, TIGAK, TLINGIT, WAHGI, WINTU


In [37]:
langs_lateral_hierarchy = []
for inventory in inventories:
    subsystems = []

    dentoalveolars = [segment for segment in inventory['Segments'] if features_d[segment]['lateral'] and features_d[segment]['coronal'] and not features_d[segment]['dorsal']]
    subsystems.append(dentoalveolars)

    retroflex = [segment for segment in inventory['Segments'] if features_d[segment]['lateral'] and not features_d[segment]['anterior'] and not features_d[segment]['dorsal']]
    subsystems.append(retroflex)

    
    palatals = [segment for segment in inventory['Segments'] if features_d[segment]['lateral'] and not features_d[segment]['anterior'] and features_d[segment]['coronal'] and not features_d[segment]['dorsal']]
    subsystems.append(palatals)
    
        
    velars = [segment for segment in inventory['Segments'] if features_d[segment]['lateral'] and features_d[segment]['dorsal'] and features_d[segment]['high'] and not features_d[segment]['continuant'] and features_d[segment]['coronal'] is False ]
    subsystems.append(velars)
    
    langs_lateral_hierarchy.append({inventory['LanguageName']: subsystems})


html_table = ['<table>']

# Build header
html_table.append('<tr>')
for header in ['Llengua', 'laterals dento', 'laterals retroflex', 'laterals palatal',
               'laterals velar', 'Jerarquia laterals (d &gt; r &gt; p  &gt; v)']:
    
    html_table.append('<td>{}</td>'.format(header))
    
else:
    html_table.append('<tr>')

candidates = 0
followers = 0
# Add contents
for lang in langs_lateral_hierarchy:
    
    candidates += 1
    for inv in lang:
        if len(lang[inv][0]) == 0 and len(lang[inv][1]) == 0 and len(lang[inv][2]) == 0 and  len(lang[inv][3]) == 0:
            continue
        
        html_table.append('<tr>')
        html_table.append('<td>{}</td>'.format(inv))
        
        for item in lang[inv]:
            html_table.append('<td>{} [ {} ]</td>'.format(len(item), ' '.join(item)))
        
        follows_hierarchy = len(lang[inv][0]) >= len(lang[inv][1]) and len(lang[inv][1]) >= len(lang[inv][2])
        html_table.append('<td>{}<td>'.format("si" if follows_hierarchy else "no"))

    else:
        if follows_hierarchy:
            followers += 1
        html_table.append('</tr>')
else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))

Llengua laterals dento laterals retroflex laterals palatal laterals velar Jerarquia laterals (d > r > p > v) Ache 1 [ ɺ̪ ] 0 [ ] 0 [ ] 0 [ ] si Alabama 2 [ l̪ ɬ̪ ] 0 [ ] 0 [ ] 0 [ ] si Angaatiha 1 [ ɺ ] 0 [ ] 0 [ ] 0 [ ] si Ao 2 [ l ɭ͓ ] 1 [ ɭ͓ ] 1 [ ɭ͓ ] 0 [ ] si Arára, Pará 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Awa Pit 2 [ ɬ l ] 0 [ ] 0 [ ] 0 [ ] si Awtuw 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Baining 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Bandjalang 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Bariai 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Biak 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Biali 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Blackfoot 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Cacua 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Cherokee 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Cubeo 1 [ ɺ̪ ] 0 [ ] 0 [ ] 0 [ ] si Dani 1 [ l̪ ] 0 [ ] 0 [ ] 0 [ ] si Dyirbal 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Ekari 0 [ ] 0 [ ] 0 [ ] 1 [ ɡˡ ] si Endo 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Faiwol 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Fuzhou 1 [ l̪ ] 0 [ ] 0 [ ] 0 [ ] si Golin 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Gugu-Yalandyi 1 [ l̪ ] 0 [ ] 0 [ ] 0 [ ] si Hawaiian 1 [ l̪ ] 0 [ ] 0 [ ] 0 [ ] si Ikpeng 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Imonda 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Karajá 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Katukína 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Kikamba 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Kipsigis 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Krahô 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Kuikúro-Kalapálo 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Kuot 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Leti 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Malakmalak 2 [ l̠ l ] 1 [ l̠ ] 1 [ l̠ ] 0 [ ] si Manam 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Namia 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Nandi 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Ningil 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Nɔmaa (NɔmaáNdɛ́) 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Oneida 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Palauan 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Pohnpeian 1 [ l̪ ] 0 [ ] 0 [ ] 0 [ ] si Sabane 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Sabaot 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Samo 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Sanuma; Sanumá 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Sebei 1 [ l̪ ] 0 [ ] 0 [ ] 0 [ ] si Seimat 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Selaru 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Shawnee 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Skou 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Southern Nuautl 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Taoripi 1 [ l̪ ] 0 [ ] 0 [ ] 0 [ ] si Tetun 1 [ l̪ ] 0 [ ] 0 [ ] 0 [ ] si Tigak 1 [ ɮ ] 0 [ ] 0 [ ] 0 [ ] si Tinputz 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Tiwi 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Tongan; Tonga 1 [ ɺ ] 0 [ ] 0 [ ] 0 [ ] si Vanimo 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Waiwai 1 [ ɺ ] 0 [ ] 0 [ ] 0 [ ] si Waris 1 [ l̪ ] 0 [ ] 0 [ ] 0 [ ] si Wik-Munkan 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Yidiny 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si Yil 1 [ l ] 0 [ ] 0 [ ] 0 [ ] si

In [38]:
langs_rothic_hierarchy = []
for inventory in inventories:
    subsystems = []

    dentoalveolars = [segment for segment in inventory['Segments'] if is_rothic(segment) and features_d[segment]['coronal'] and features_d[segment]['anterior']     and not features_d[segment]['dorsal']]
    subsystems.append(dentoalveolars)

    retroflex =      [segment for segment in inventory['Segments'] if is_rothic(segment) and features_d[segment]['coronal'] and not features_d[segment]['anterior'] and not features_d[segment]['dorsal']]
    subsystems.append(retroflex)
    
    uvulars =        [segment for segment in inventory['Segments'] if is_rothic(segment) and not features_d[segment]['coronal'] and not features_d[segment]['coronal'] and features_d[segment]['dorsal']]
    subsystems.append(uvulars)
    
    langs_rothic_hierarchy.append({inventory['LanguageName']: subsystems})


html_table = ['<table>']

# Build header
html_table.append('<tr>')
for header in ['Llengua', 'rothics dento', 'rothics retroflex', 'rothics uvulars',
               'Jerarquia rothics (d &gt; r &gt; u)']:
    
    html_table.append('<td>{}</td>'.format(header))
    
else:
    html_table.append('<tr>')

candidates = 0
followers = 0
# Add contents
for lang in langs_rothic_hierarchy:
    
    for inv in lang:
        if len(lang[inv][0]) == 0 and len(lang[inv][1]) == 0 and len(lang[inv][2]) == 0:
            continue
            
        candidates += 1

        html_table.append('<tr>')
        html_table.append('<td>{}</td>'.format(inv))
        
        for item in lang[inv]:
            html_table.append('<td>{} [ {} ]</td>'.format(len(item), ' '.join(item)))
        
        follows_hierarchy = len(lang[inv][0]) >= len(lang[inv][1]) and len(lang[inv][1]) >= len(lang[inv][2])
        html_table.append('<td>{}<td>'.format("si" if follows_hierarchy else "no"))

    else:
        if follows_hierarchy:
            followers += 1
        html_table.append('</tr>')
else:
    html_table.append('</table></font>')

display(HTML(''.join(html_table)))

print('Segueixen la jerarquia {:.2%} ({} de {})'.format(followers / candidates, followers, candidates))

Llengua rothics dento rothics retroflex rothics uvulars Jerarquia rothics (d > r > u) Abau 1 [ ɾ ] 0 [ ] 0 [ ] si Aguaruna 1 [ ɾ ] 0 [ ] 0 [ ] si Ainu 1 [ ɾ ] 0 [ ] 0 [ ] si Akawaio 1 [ *R̪ ] 0 [ ] 0 [ ] si Akurio 1 [ ɾ ] 0 [ ] 0 [ ] si Amahuaca 1 [ ɾ̪ ] 0 [ ] 0 [ ] si Amanab 1 [ r ] 0 [ ] 0 [ ] si Apalaí 1 [ ɾ ] 0 [ ] 0 [ ] si Apinaye 0 [ ] 1 [ ɽ ] 0 [ ] no Arabela 1 [ r̪ ] 0 [ ] 0 [ ] si Arára, Pará 1 [ ɾ ] 0 [ ] 0 [ ] si Arikapú 1 [ ɾ ] 0 [ ] 0 [ ] si Asmat 1 [ ɾ ] 0 [ ] 0 [ ] si Au 1 [ ɾ ] 0 [ ] 0 [ ] si Auyana 1 [ ɾ ] 0 [ ] 0 [ ] si Awtuw 1 [ ɾ ] 0 [ ] 0 [ ] si Baining 1 [ ɾ ] 0 [ ] 0 [ ] si Bandjalang 1 [ r ] 0 [ ] 0 [ ] si Barasano 1 [ ɾ ] 0 [ ] 0 [ ] si Bariai 1 [ r ] 0 [ ] 0 [ ] si Barí 1 [ r ] 0 [ ] 0 [ ] si Baruga 1 [ ɾ ] 0 [ ] 0 [ ] si Bésɨro 1 [ ɾ ] 0 [ ] 0 [ ] si Biak 1 [ r ] 0 [ ] 0 [ ] si Biali 1 [ ɾ ] 0 [ ] 0 [ ] si Binandere 1 [ ɾ ] 0 [ ] 0 [ ] si Binumarien 1 [ r ] 0 [ ] 0 [ ] si Bororo 1 [ *R̪ ] 0 [ ] 0 [ ] si Canela 1 [ ɾ ] 0 [ ] 0 [ ] si Carijona 1 [ ɾ ] 0 [ ] 0 [ ] si Chuave 1 [ ɾ ] 0 [ ] 0 [ ] si Dadibi 1 [ ɾ ] 0 [ ] 0 [ ] si Dyirbal 1 [ r ] 1 [ ɻ ] 0 [ ] si Endo 1 [ r ] 0 [ ] 0 [ ] si Fasu 1 [ ɾ ] 0 [ ] 0 [ ] si Gavião do Pará 1 [ ɾ ] 0 [ ] 0 [ ] si Golin 1 [ r ] 0 [ ] 0 [ ] si Guajajara 1 [ ɾ ] 0 [ ] 0 [ ] si Gugu-Yalandyi 1 [ *R̪ ] 1 [ ɻ ] 0 [ ] si Huron 1 [ r ] 0 [ ] 0 [ ] si Ikpeng 1 [ ɾ ] 0 [ ] 0 [ ] si Imonda 1 [ r ] 0 [ ] 0 [ ] si Ingarikó 1 [ ɾ ] 0 [ ] 0 [ ] si Irarutu 1 [ ɾ̪ ] 0 [ ] 0 [ ] si Iwam 1 [ *R ] 0 [ ] 0 [ ] si Jabutí 1 [ ɾ ] 0 [ ] 0 [ ] si Jamamadí 1 [ ɾ ] 0 [ ] 0 [ ] si Kaiabi 1 [ ɾ ] 0 [ ] 0 [ ] si Karajá 1 [ ɾ ] 0 [ ] 0 [ ] si Karitiana; Karitiâna 1 [ ɾ ] 0 [ ] 0 [ ] si Kaxuiâna 1 [ ɾ ] 0 [ ] 0 [ ] si Kipsigis 1 [ r ] 0 [ ] 0 [ ] si Koiari 1 [ ɾ ] 0 [ ] 0 [ ] si Kokama-Kokamilla 1 [ ɾ ] 0 [ ] 0 [ ] si Krinkati-Timbira 1 [ ɾ ] 0 [ ] 0 [ ] si Kuot 1 [ r ] 0 [ ] 0 [ ] si Leti 1 [ r ] 0 [ ] 0 [ ] si Macushi 1 [ ɾ ] 0 [ ] 0 [ ] si Malakmalak 1 [ r ] 0 [ ] 0 [ ] si Manam 1 [ ɾ ] 0 [ ] 0 [ ] si Maori 1 [ ɾ ] 0 [ ] 0 [ ] si Mapoyo 1 [ ɾ ] 0 [ ] 0 [ ] si Namia 1 [ r ] 0 [ ] 0 [ ] si Nandi 1 [ ɾ ] 0 [ ] 0 [ ] si Nasioi 1 [ ɾ̪ ] 0 [ ] 0 [ ] si Nimboran 1 [ *R̪ ] 0 [ ] 0 [ ] si Ningil 1 [ r ] 0 [ ] 0 [ ] si North Marquesan 1 [ r ] 0 [ ] 0 [ ] si Nukak 1 [ ɾ ] 0 [ ] 0 [ ] si Oro Win 2 [ t̪ʙ ɾ ] 0 [ ] 0 [ ] si Palauan 1 [ r ] 0 [ ] 0 [ ] si Panará 1 [ ɾ ] 0 [ ] 0 [ ] si Pémono 1 [ ɾ ] 0 [ ] 0 [ ] si Pohnpeian 1 [ r ] 0 [ ] 0 [ ] si Rikbaktsa 1 [ ɾ ] 1 [ ɽ ] 0 [ ] si Roro 1 [ ɾ̪ ] 0 [ ] 0 [ ] si Rotokas 1 [ ᴅ ] 0 [ ] 0 [ ] si Sabaot 1 [ r ] 0 [ ] 0 [ ] si Sebei 2 [ ɾ̪ r̪ ] 0 [ ] 0 [ ] si Selaru 1 [ r ] 0 [ ] 0 [ ] si Shanenawa 1 [ ɾ ] 0 [ ] 0 [ ] si Shawi 1 [ ɾ ] 0 [ ] 0 [ ] si Shiriana 1 [ ɾ̪ ] 0 [ ] 0 [ ] si Shuar 1 [ ɾ ] 0 [ ] 0 [ ] si Skou 1 [ r ] 0 [ ] 0 [ ] si Southern Kiwai 1 [ *R̪ ] 0 [ ] 0 [ ] si Southern Nuautl 1 [ r ] 0 [ ] 0 [ ] si Suena 1 [ ɾ̪ ] 0 [ ] 0 [ ] si Suyá 1 [ ɾ ] 0 [ ] 0 [ ] si Taushiro 1 [ ɾ ] 0 [ ] 0 [ ] si Tetun 1 [ r̪ ] 0 [ ] 0 [ ] si Tigak 1 [ r ] 0 [ ] 0 [ ] si Tiwi 1 [ ɾ ] 1 [ ɻ ] 0 [ ] si Trió 1 [ ɾ ] 0 [ ] 0 [ ] si Waiwai 1 [ ɾ ] 0 [ ] 0 [ ] si Wari; Wari'; Wariʔ; Oro Nao 1 [ ɾ ] 0 [ ] 0 [ ] si Warihio 1 [ ɾ ] 0 [ ] 0 [ ] si Waris 1 [ *R̪ ] 0 [ ] 0 [ ] si Wik-Munkan 1 [ r ] 0 [ ] 0 [ ] si Yabarana 1 [ ɾ ] 0 [ ] 0 [ ] si Yareba 1 [ ɾ ] 0 [ ] 0 [ ] si Yawa 1 [ ɾ ] 0 [ ] 0 [ ] si Yekwana 1 [ ɾ ] 0 [ ] 0 [ ] si Yidiny 1 [ r ] 1 [ ɻ ] 0 [ ] si Yil 1 [ r ] 0 [ ] 0 [ ] si

Segueixen la jerarquia 151.43% (159 de 105)


In [46]:
morph = """
Alagwa
Alamblak
Amharic
Apurinã
Arabic (Egyptian)
Arabic (Gulf)
Arabic (Syrian)
Arbore
Bayso
Beja
Berber (Middle Atlas)
Campa (Axininca)
Chinantec (Lealao)
Cree (Plains)
Diyari
Dizi
French
Gaelic (Scots)
Hausa
Hebrew (Modern)
Hindi
Hixkaryana
Iraqw
Kashmiri
Khasi
Khmu'
Kolami
Latvian
Lele
Macushi
Maltese
Maybrat
Miya
Mosetén
Mundari
Ojibwa (Eastern)
Oromo (Harar)
Panjabi
Pashto
Passamaquoddy-Maliseet
Pitta Pitta
Qafar
Rendille
Spanish
Tagalog
Taiap
Tigré
Tiwi
Tunica
Yazgulyam
Abkhaz
Barasano
Defaka
English
German
Godoberi
Grebo
Greek (Modern)
Icelandic
Kannada
Ket
Khoekhoe
Koromfe
Lavukaleve
Mangarrayi
Marathi
Nicobarese (Car)
Oneida
Retuarã
Russian
Seneca
Tamil
Tidore
Ukrainian
Wardaman
Wari
Archi
Bininj Gun-Wok
Burushaski
Dyirbal
Godié
Lak
Marind
Paumarí
Pirahã
Tsez
Wambaya
Zande
Arapesh (Mountain)
Babungo
Chichewa
Diola-Fogny
Fula (Guinean)
Hunzib
Ingush
Juhoan
Kisi
Kongo
Lingala
Luvale
Maung
Mixtec (Chalcatongo)
Ngangityemerri
Nkore-Kiga
Nunggubuyu
Nyamwezi
Nyiha
Shona
Supyire
Swahili
Yimas
Zulu
""".split()

for lang in morph:
    for inventory in inventories:
        if inventory['LanguageName'] == lang:
            print(inventory[L])
    
    

{'Area': 'America', 'LanguageFamilyGenus': 'Cariban', 'Consonants': '10', 'LanguageFamilyRoot': 'Cariban', 'InventoryID': '1877', 'LanguageCode': 'mbc', 'Longitude': '-59:15', 'Segments': ['ʔ', 'k', 'j', 'm', 'n', 'p', 's', 't', 'w', 'ɾ'], 'LanguageName': 'Macushi', 'Latitude': '04:00', 'Source': 'SAPHON'}
{'Area': 'Pacific', 'LanguageFamilyGenus': 'Tiwian', 'Consonants': '14', 'LanguageFamilyRoot': 'Australian', 'InventoryID': '1218', 'LanguageCode': 'tiw', 'Longitude': '131:0', 'Segments': ['n̪', 'j', 'k', 'm', 'ɣ', 'n', 'p', 't̪', 't', 'w', 'ɻ', 'ɾ', 'ŋ', 'l'], 'LanguageName': 'Tiwi', 'Latitude': '-11:40', 'Source': 'PH'}
{'Area': 'America', 'LanguageFamilyGenus': 'Tucanoan', 'Consonants': '11', 'LanguageFamilyRoot': 'Tucanoan', 'InventoryID': '239', 'LanguageCode': 'bao', 'Longitude': '-70:20', 'Segments': ['ɡ', 'b', 'd', 'k', 'j', 'p', 's', 't', 'w', 'h', 'ɾ'], 'LanguageName': 'Barasano', 'Latitude': '00:25', 'Source': 'UPSID'}
{'Area': 'America', 'LanguageFamilyGenus': 'Northern 